In [1]:
import pandas as pd
import numpy as np
from dateutil.relativedelta import *
from datetime import date, timedelta
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score, f1_score,recall_score,fbeta_score,precision_score
from sklearn.metrics import f1_score,confusion_matrix
from sklearn.model_selection import train_test_split
import statsmodels.api as sm
from sklearn.metrics import roc_auc_score,roc_curve
from statsmodels.stats.outliers_influence import variance_inflation_factor
import os
import xlrd

In [2]:
start_date="2020-08-10"
end_date="2021-06-28"
train_stop_date="2021-01-25"

##SALES NEW DATA MERGING
path_sales="//home//jovyan//ageing-inventory-project//Data//Sales_Ageing_BP6/Sales_raw_new/"
sales_ls = os.listdir(path_sales)
#print(sales_ls)
sales_merge=pd.DataFrame()
for f in sales_ls :
    try:
        df=pd.read_excel(path_sales+"/"+f)
        df["filename"]=f
        sales_merge=pd.concat([sales_merge,df])
    except:
        print("error_ipynb")
    
region_df=pd.read_csv(r"/home/jovyan/ageing-inventory-project/Data/Sales_Ageing_BP6/Sales_Region_Master.csv")
waste_df=pd.read_csv(r"/home/jovyan/ageing-inventory-project/Data/Sales_Ageing_BP6/Sales_waste_master.csv")

sales_merge=pd.merge(sales_merge,region_df,how="left",on=["Sales Office"])
sales_merge=pd.merge(sales_merge,waste_df,how="left",on=["Material Group"])


AAG=["DO","EX"]
DC=[10,15,20,25]
sales_merge = sales_merge.loc[sales_merge['Account Assg Group'].isin(AAG) & sales_merge["Distribution Channel"].isin(DC)]
#ales_merge["Product/Waste"]=sales_merge["Product/Waste"].astype('str')
sales_merge=sales_merge.loc[sales_merge["Division"]==13]
sales_merge=sales_merge.loc[sales_merge["Product/Waste"].astype(str)=="Product"]

sales_merge["WEEKDAY"]=sales_merge["Billing Date"]+pd.offsets.Week(weekday=0,n=1)
sales_merge_new=sales_merge[["Billing Date","WEEKDAY","Material Code","Distribution Channel","Division","Group Code","Material Group","Plant","Plant Categeory","Region","Sales Office","Billing Quantity in MT"]]
sales_merge_new=sales_merge_new.rename(columns={"Billing Quantity in MT":"Total"})
sales_merge_new=sales_merge_new.loc[(sales_merge_new["WEEKDAY"]>=start_date) & (sales_merge_new["WEEKDAY"]<=end_date)]


##PRODUCTION NEW DATA MERGING

path_prod="//home//jovyan//ageing-inventory-project//Data/Production_Ageing_BP6//Prod_Aug_Oct/"
prod_ls = os.listdir(path_prod)
#print(prod_ls)
prod_merge=pd.DataFrame()
for f in prod_ls :
    try:
        df=pd.read_csv(path_prod+"//"+f,encoding='utf8', engine='python')
        df["filename"]=f
        prod_merge=pd.concat([prod_merge,df])
    except:
        print("ls")
    
prod_merge["Posting Date"]=pd.to_datetime(prod_merge["Posting Date"],format="%d-%m-%Y")
#prod_merge['Month'] = prod_merge['Posting Date'].dt.month
#prod_merge['Year'] = prod_merge['Posting Date'].dt.year
prod_merge['Production QTY']=prod_merge['Production QTY'].str.replace(',', '').astype(float)
prod_merge['Plant']=prod_merge['Plant'].astype(str)
prod_merge['Storage Location']=prod_merge['Storage Location'].astype(str)
MG=["PSF","PSF TOW"]
Plants=["1405","2202","2201","3996","3912","3911","3905","3913","3998","1449","3997","4109"]
Storage_loc=["2200","2383","23A6"]
prod_merge = prod_merge[prod_merge['Material Group'].isin(MG) ]
prod_merge = prod_merge[prod_merge['Plant'].isin(Plants)]
prod_merge = prod_merge[prod_merge['Storage Location'].isin(Storage_loc)]
prod_merge["WEEKDAY"]=prod_merge["Posting Date"]+pd.offsets.Week(weekday=0,n=1)
prod_merge["Production_Qty_MT"]=prod_merge["Production QTY"]/1000
prod_merge=prod_merge.loc[(prod_merge["WEEKDAY"]>=start_date) & (prod_merge["WEEKDAY"]<=end_date)]


prod_merge_new=prod_merge[['Posting Date', 'WEEKDAY', 'Division', 'Material Group', 'Plant',
       'Material', 'Material Description', 'Storage Location', 'Batch', 'Unit',
       'Production QTY', 'Production_Qty_MT', 'No.of Pallets']]

##AGEING NEW DATA MERGE

path = '//home//jovyan//ageing-inventory-project//Data//Ageing_Final//Ageing_Aug_Oct/'

files = []
Ageing_Stock=pd.DataFrame()
# r=root, d=directories, f = files
for r, d, f in os.walk(path):
    for file in f:
        if '.xlsx' in file:
            files.append(os.path.join(r, file))
            

k=0
for f in files:
    file_name=f.split("/")[-1]
    k =k+1
    #print(file_name)
    #print(f)
   
    
    try:
        xls = xlrd.open_workbook(f, on_demand=True)

        #print(files[0])
        sheet_list=xls.sheet_names()
        sheet_list = [x.upper() for x in sheet_list] 
            #print(sheet_list)
            #data_filtered-pd.DataFrame()
            #print(f)

        if "DATA" in sheet_list :
            i=sheet_list.index("DATA")
            data=pd.read_excel(f,sheet_name=i)
            data.columns = data.columns.str.upper()
            column_list=list(data.columns)


            if "S LOC" in column_list:
                data.rename(columns={'S LOC': 'STORAGE LOCATION'}, inplace=True)
            if "DIV" in column_list:
                data.rename(columns={'DIV': "DIVISION_2"}, inplace=True)
            if "DIV." in column_list:
                data.rename(columns={'DIV.': "DIVISION_2"}, inplace=True)
            if "TOTAL" in column_list:
                data.rename(columns={'TOTAL': "TOTAL STOCK"}, inplace=True)
            column_list_updated=list(data.columns)

            master_list=["DIVISION","DIVISION_2","PLANT", "STORAGE LOCATION","MATERIAL","BATCH","UOM","SOURCE PLANT","0-15 DAYS","16-30 DAYS","31-46 DAYS","46-60 DAYS","61-90 DAYS","91-150 DAYS","150-180 DAYS"," >365 DAYS","TOTAL STOCK"]
            column_list_updated=list(data.columns)
            #print(list(set(master_list) - set(column_list_updated)))
            difference=list(set(master_list) - set(column_list_updated))
            for new_column in difference:
                data[new_column]= None


            data_filtered=data[master_list]
            data_filtered["File_Name"]=file_name

            Ageing_Stock=pd.concat([Ageing_Stock,data_filtered])

        if "BI DATA" in sheet_list:

            i=sheet_list.index("BI DATA")
            data=pd.read_excel(f,sheet_name=i)
            data.columns = data.columns.str.upper()
            column_list=list(data.columns)


            if "S LOC" in column_list:
                data.rename(columns={'S LOC': 'STORAGE LOCATION'}, inplace=True)
            if "DIV" in column_list:
                data.rename(columns={'DIV': "DIVISION_2"}, inplace=True)
            if "DIV." in column_list:
                data.rename(columns={'DIV.': "DIVISION_2"}, inplace=True)
            if "TOTAL" in column_list:
                data.rename(columns={'TOTAL': "TOTAL STOCK"}, inplace=True)
            column_list_updated=list(data.columns)

            master_list=["DIVISION","DIVISION_2","PLANT", "STORAGE LOCATION","MATERIAL","BATCH","UOM","SOURCE PLANT","0-15 DAYS","16-30 DAYS","31-46 DAYS","46-60 DAYS","61-90 DAYS","91-150 DAYS","150-180 DAYS"," >365 DAYS","TOTAL STOCK"]
            column_list_updated=list(data.columns)
            #print(list(set(master_list) - set(column_list_updated)))
            difference=list(set(master_list) - set(column_list_updated))
            for new_column in difference:
                data[new_column]= None


            data_filtered=data[master_list]
            data_filtered["File_Name"]=file_name

            Ageing_Stock=pd.concat([Ageing_Stock,data_filtered])
        if "AGEING" in sheet_list:

            i=sheet_list.index("AGEING")
            data=pd.read_excel(f,sheet_name=i)
            data.columns = data.columns.str.upper()
            column_list=list(data.columns)


            if "S LOC" in column_list:
                data.rename(columns={'S LOC': 'STORAGE LOCATION'}, inplace=True)
            if "DIV" in column_list:
                data.rename(columns={'DIV': "DIVISION_2"}, inplace=True)
            if "DIV." in column_list:
                data.rename(columns={'DIV.': "DIVISION_2"}, inplace=True)
            if "TOTAL" in column_list:
                data.rename(columns={'TOTAL': "TOTAL STOCK"}, inplace=True)
            column_list_updated=list(data.columns)

            master_list=["DIVISION","DIVISION_2","PLANT", "STORAGE LOCATION","MATERIAL","BATCH","UOM","SOURCE PLANT","0-15 DAYS","16-30 DAYS","31-46 DAYS","46-60 DAYS","61-90 DAYS","91-150 DAYS","150-180 DAYS"," >365 DAYS","TOTAL STOCK"]
            column_list_updated=list(data.columns)
            #print(list(set(master_list) - set(column_list_updated)))
            difference=list(set(master_list) - set(column_list_updated))
            for new_column in difference:
                data[new_column]= None


            data_filtered=data[master_list]
            data_filtered["File_Name"]=file_name

            Ageing_Stock=pd.concat([Ageing_Stock,data_filtered])
        if "BASE" in sheet_list:

            i=sheet_list.index("BASE")
            data=pd.read_excel(f,sheet_name=i)
            data.columns = data.columns.str.upper()
            column_list=list(data.columns)


            if "S LOC" in column_list:
                data.rename(columns={'S LOC': 'STORAGE LOCATION'}, inplace=True)
            if "DIV" in column_list:
                data.rename(columns={'DIV': "DIVISION_2"}, inplace=True)
            if "DIV." in column_list:
                data.rename(columns={'DIV.': "DIVISION_2"}, inplace=True)
            if "TOTAL" in column_list:
                data.rename(columns={'TOTAL': "TOTAL STOCK"}, inplace=True)
            column_list_updated=list(data.columns)

            master_list=["DIVISION","DIVISION_2","PLANT", "STORAGE LOCATION","MATERIAL","BATCH","UOM","SOURCE PLANT","0-15 DAYS","16-30 DAYS","31-46 DAYS","46-60 DAYS","61-90 DAYS","91-150 DAYS","150-180 DAYS",">365 DAYS","TOTAL STOCK"]
            column_list_updated=list(data.columns)
            #print(list(set(master_list) - set(column_list_updated)))
            difference=list(set(master_list) - set(column_list_updated))
            for new_column in difference:
                data[new_column]= None


            data_filtered=data[master_list]
            data_filtered["File_Name"]=file_name

            Ageing_Stock=pd.concat([Ageing_Stock,data_filtered])

    except:
        print(file_name +  "Corrupted File")

Ageing_Stock['WEEKDAY'] = Ageing_Stock.File_Name.str.extract('(\d+)')
Ageing_Stock['WEEKDAY'] = pd.to_datetime(Ageing_Stock['WEEKDAY'],format='%Y%m%d') 
Ageing_Stock=Ageing_Stock.loc[(Ageing_Stock["WEEKDAY"]>=start_date) & (Ageing_Stock["WEEKDAY"]<=end_date)]
Ageing_Stock=Ageing_Stock.loc[Ageing_Stock["DIVISION_2"]==13]
Ageing_Stock=Ageing_Stock.rename(columns={" >365 DAYS":">365 DAYS","TOTAL STOCK":"New_Total_Stocks(KG)"})
Ageing_merge_new=Ageing_Stock[["MATERIAL","WEEKDAY","0-15 DAYS","16-30 DAYS","31-46 DAYS","46-60 DAYS","61-90 DAYS","91-150 DAYS","150-180 DAYS",">365 DAYS","New_Total_Stocks(KG)"]]
Ageing_merge_new=Ageing_merge_new.fillna(0.0)

##CRUDE AND COTTON DATA MERGE NEW
crude_df=pd.read_excel(r"/home/jovyan/ageing-inventory-project/Data/Crude_Cotton/New_Crude_Master.xlsx")
cotton_df=pd.read_excel(r"/home/jovyan/ageing-inventory-project/Data/Crude_Cotton/New_PSF_Cotton_Master.xlsx")

cotton_df["Monday_Dates"]=cotton_df["DATE"]+pd.offsets.Week(weekday=0,n=1)
cotton_avg_df=pd.DataFrame()
group_cot= cotton_df.groupby(["Monday_Dates"])
cotton_avg_df["Avg PSF Price (Rs/Kg)"]=group_cot["PSF Price(Rs/kg)"].agg(np.mean)
cotton_avg_df["Avg Cotton Price (Rs/Candy)"]=group_cot["Cotton Price(Rs/Candy)"].agg(np.mean)

crude_df["Price Point"]=pd.to_datetime(crude_df["Price Point"],format="%d/%m/%Y")
crude_df["Monday_Dates"]=crude_df["Price Point"]+pd.offsets.Week(weekday=0,n=1)
crude_avg_df=pd.DataFrame()
group_crude= crude_df.groupby(["Monday_Dates"])
crude_avg_df["Avg of Crude_Price"]=group_crude["West Europe; Crude Oil - Brent Daily; $/barrel"].agg(np.mean)

crude_data_new=pd.merge(cotton_avg_df,crude_avg_df, how="inner",on=["Monday_Dates"])
crude_data_new=crude_data_new.reset_index(level=['Monday_Dates'])
crude_data_new=crude_data_new.loc[(crude_data_new["Monday_Dates"]>=start_date) & (crude_data_new["Monday_Dates"]<=end_date)]


                     

error_ipynb
ls


/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:161: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [3]:
Ageing_Merge_old=pd.read_excel(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Required_Data_Files/Ageing_Final_Merge.xlsx")
Production_Merge_old=pd.read_excel(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Required_Data_Files/Production_Merge.xlsx")
sales_old = pd.read_excel(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Required_Data_Files/Sales_Merge.xlsx")
d_l_df_old=pd.read_csv(r'/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Required_Data_Files/Merges_Lusture_Denier.csv')##READING CSV FILE
crude_data_old=pd.read_excel(r'/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Required_Data_Files/Crude_Cotton_Data_Weekl_Wise.xlsx')


In [4]:
Ageing_Merge=Ageing_Merge_old[["MATERIAL","WEEKDAY","0-15 DAYS","16-30 DAYS","31-46 DAYS","46-60 DAYS","61-90 DAYS","91-150 DAYS","150-180 DAYS",">365 DAYS","New_Total_Stocks(KG)"]]
Production_Merge=Production_Merge_old[['Posting Date', 'WEEKDAY', 'Division', 'Material Group', 'Plant',
       'Material', 'Material Description', 'Storage Location', 'Batch', 'Unit',
       'Production QTY', 'Production_Qty_MT', 'No.of Pallets']]
sales=sales_old[["Billing Date","WEEKDAY","Material Code","Distribution Channel","Division","Group Code","Material Group","Plant","Plant Categeory","Region","Sales Office","Total"]]
crude_data=crude_data_old[["Monday_Dates","Avg PSF Price (Rs/Kg)","Avg Cotton Price (Rs/Candy)","Avg of Crude_Price"]]

In [5]:
Ageing_Merge=pd.concat([Ageing_Merge,Ageing_merge_new])
Production_Merge=pd.concat([Production_Merge,prod_merge_new])
sales=pd.concat([sales,sales_merge_new])
crude_data=pd.concat([crude_data,crude_data_new])
d_l_df=d_l_df_old.copy()


In [6]:

##AGEING DATA WEEKLY AGGREGATION

Ageing_aggregation=pd.DataFrame()
group= Ageing_Merge.groupby(["WEEKDAY","MATERIAL"])

Ageing_aggregation["TOTAL STOCK"]=group["New_Total_Stocks(KG)"].agg(np.sum)
Ageing_aggregation["0-15 DAYS"]=group["0-15 DAYS"].agg(np.sum)
Ageing_aggregation["16-30 DAYS"]=group["16-30 DAYS"].agg(np.sum)
Ageing_aggregation["31-46 DAYS"]=group["31-46 DAYS"].agg(np.sum)
Ageing_aggregation["46-60 DAYS"]=group["46-60 DAYS"].agg(np.sum)
Ageing_aggregation["61-90 DAYS"]=group["61-90 DAYS"].agg(np.sum)
Ageing_aggregation["91-150 DAYS"]=group["91-150 DAYS"].agg(np.sum)
Ageing_aggregation["150-180 DAYS"]=group["150-180 DAYS"].agg(np.sum)
Ageing_aggregation[">365 DAYS"]=group[">365 DAYS"].agg(np.sum)


Ageing_aggregation=Ageing_aggregation.reset_index(level=['WEEKDAY', 'MATERIAL'])
Ageing_aggregation["AGED STOCK"]= Ageing_aggregation["TOTAL STOCK"]-(Ageing_aggregation["0-15 DAYS"]+ Ageing_aggregation["16-30 DAYS"]+Ageing_aggregation["31-46 DAYS"]+Ageing_aggregation["46-60 DAYS"])
Ageing_aggregation['AGEING FLAG'] = Ageing_aggregation['AGED STOCK'].apply(lambda x: "YES" if x > 400 else "NO")

##PRODUCTION DATA WEEKLY AGGREGATION

#Production_Merge=Production_Merge.drop(["Unnamed: 0"],axis=1)
Production_Merge["WEEKDAY"]=pd.to_datetime(Production_Merge["WEEKDAY"])
#Production_Merge["No.of Pallets"]=Production_Merge["No.of Pallets"].astype(int)
Production_aggregation=pd.DataFrame()
group= Production_Merge.groupby(["WEEKDAY","Material","Material Description"])
Production_aggregation["TOTAL PRODUCTION"]=group["Production_Qty_MT"].agg(np.sum)
#Production_aggregation["NUMBER OF PALLETS"]=group["No.of Pallets"].agg(np.sum)
Production_aggregation["COUNT OF TRANSACTIONS"]=group["WEEKDAY"].count()
Production_aggregation=Production_aggregation.reset_index(level=['WEEKDAY', 'Material',"Material Description"])
Production_aggregation=Production_aggregation.loc[((Production_aggregation["WEEKDAY"]>="2017-07-03") & (Production_aggregation["WEEKDAY"]<="2020-03-30"))|(Production_aggregation["WEEKDAY"]>=start_date)]

##SALES DATA WEEKLY AGGREGATION

sales['WEEKDAY'] = pd.to_datetime(sales['WEEKDAY'])
sales=sales.loc[((sales["WEEKDAY"]>="2017-07-03") & (sales["WEEKDAY"]<="2020-03-30"))|(sales["WEEKDAY"]>=start_date)]
X = sales.groupby(['WEEKDAY','Material Code'])['Plant Categeory'].value_counts()
X = pd.DataFrame(X)

#print(X)

X = X.rename(columns = {'Plant Categeory':'Plant_Category_Count'})
d1 = X.pivot_table(index = ['WEEKDAY','Material Code'],columns = ['Plant Categeory'],values = ['Plant_Category_Count'],aggfunc = np.sum,fill_value = 0)
#print(d1)
Y = sales.groupby(['WEEKDAY','Material Code','Plant Categeory']).Total.sum()
Y = pd.DataFrame(Y)
d2 = Y.pivot_table(index = ['WEEKDAY','Material Code'],columns = ['Plant Categeory'],values = ['Total'],aggfunc = np.sum,fill_value = 0)

X1 = sales.groupby(['WEEKDAY','Material Code'])['Sales Office'].value_counts()
X1 = pd.DataFrame(X1)
X1 = X1.rename(columns = {'Sales Office':'Sales_Office_Count'})
d3 = X1.pivot_table(index = ['WEEKDAY','Material Code'],columns = ['Sales Office'],values = ['Sales_Office_Count'],aggfunc = np.sum,fill_value = 0)
Y1 = sales.groupby(['WEEKDAY','Material Code','Sales Office']).Total.sum()
Y1 = pd.DataFrame(Y1)
d4 = Y1.pivot_table(index = ['WEEKDAY','Material Code'],columns = ['Sales Office'],values = ['Total'],aggfunc = np.sum,fill_value = 0)

sales_aggregation=pd.DataFrame()
group= sales.groupby(["WEEKDAY","Material Code"])
sales_aggregation["Total Quantity"]=group["Total"].agg(np.sum)
sales_aggregation["Transaction Count"]=group["Billing Date"].count()
sales_aggregation["Count_Group_Code"]=group['Group Code'].nunique()
sales_aggregation["Region_Count"]=group["Region"].nunique()
sales_aggregation["Unique_Sales_Plant_Count"]=group["Plant"].nunique()
sales_aggregation=pd.merge(sales_aggregation,d1[d1.columns],how='left',on=["WEEKDAY","Material Code"])
sales_aggregation=pd.merge(sales_aggregation,d2[d2.columns],how='left',on=["WEEKDAY","Material Code"])
sales_aggregation=pd.merge(sales_aggregation,d3[d3.columns],how='left',on=["WEEKDAY","Material Code"])
sales_aggregation=pd.merge(sales_aggregation,d4[d4.columns],how='left',on=["WEEKDAY","Material Code"])
sales_aggregation=sales_aggregation.reset_index(level=['WEEKDAY', 'Material Code'])

#sales_aggregation




/opt/conda/lib/python3.7/site-packages/pandas/core/reshape/merge.py:617: UserWarning: merging between different levels can give an unintended result (1 levels on the left, 2 on the right)
  warnings.warn(msg, UserWarning)


In [7]:
#MATERIAL MASTER CREATION
##AGEING DATA MATERIAL MASTER
Ageing_eda=pd.DataFrame()
group=Ageing_aggregation.groupby(["MATERIAL"])
Ageing_eda["No. OF AGEING WEEKS"]=group["AGEING FLAG"].apply(lambda x: (x=='YES').sum())
Ageing_eda["FIRST AGEING WEEK"]=group.apply(lambda x: x[x['AGEING FLAG'] == 'YES']['WEEKDAY'].min())
Ageing_eda["LAST AGEING WEEK"]=group.apply(lambda x: x[x['AGEING FLAG'] == 'YES']['WEEKDAY'].max())
Ageing_eda["AGEING RATIO_%"]=(Ageing_eda["No. OF AGEING WEEKS"]/(((Ageing_eda["LAST AGEING WEEK"]-Ageing_eda["FIRST AGEING WEEK"]).dt.days/7)+1))*100
Ageing_eda["AGEING RATIO_%"] = Ageing_eda["AGEING RATIO_%"].fillna(0)


##SALES DATA MATERIAL MASTER
x =sales_aggregation
m = pd.DataFrame()
x['WEEKDAY'] = pd.to_datetime(x['WEEKDAY'])
m = x.groupby('Material Code')['WEEKDAY'].agg(['min','max']).rename(columns = {'min':'FIRST SALES WEEK','max':'LAST SALES WEEK'})
m["SALES WEEK COUNT"] = x.groupby('Material Code')['WEEKDAY'].count()
m['TOTAL WEEKS'] = (m['LAST SALES WEEK']-m['FIRST SALES WEEK']).dt.days 
m['TOTAL WEEKS'] = (m['TOTAL WEEKS']/7)+1
m["TOTAL SALES QUANTITY"] = x.groupby('Material Code')['Total Quantity'].sum()
m["SALES TRANSACTION COUNT"] = x.groupby('Material Code')['Transaction Count'].sum()
m["SALES TRANSACTION PER WEEK"] = m["SALES TRANSACTION COUNT"]/m["SALES WEEK COUNT"]
m["SALES QUANTITY PER WEEK"] = m["TOTAL SALES QUANTITY"]/m["SALES WEEK COUNT"]
m["SALES ACTIVITY_%"] = (m["SALES WEEK COUNT"]/m["TOTAL WEEKS"])*100
m["SALES INACTIVITY_%"]=100-m["SALES ACTIVITY_%"]
m['current'] = end_date
m['current'] = pd.to_datetime(m['current'])
m["(Last Date - Current Date)"] = (m['current'] - m['LAST SALES WEEK']).dt.days
m["INACTIVE WEEKS FROM LAST AVAILABLE WEEKDAY"]= (m["(Last Date - Current Date)"]/7)+1
m = m.drop(['current','(Last Date - Current Date)'], axis=1)

#PRODUCTION DATA MATERIAL MASTER
Prod_eda=pd.DataFrame()
group=Production_aggregation.groupby(["Material"])
Prod_eda["PRODUCTION QUANTITY"]=group["TOTAL PRODUCTION"].agg(np.sum)
Prod_eda["NO OF PRODUCTION WEEK"]=group["WEEKDAY"].nunique()
Prod_eda["PRODUCTION QUANTITY PER WEEK"]=Prod_eda["PRODUCTION QUANTITY"]/Prod_eda["NO OF PRODUCTION WEEK"]

##CONCATINATION OF ALL THREE MATERIAL MASTERS
Material_Master=pd.concat([Prod_eda,m,Ageing_eda],axis=1, sort=False)
Material_Master=Material_Master.reset_index()
Material_Master=Material_Master.rename(columns={'index':'MATERIAL'})
Material_Master['current'] = end_date
Material_Master['current'] = pd.to_datetime(Material_Master['current'])
Material_Master["Material_Sales_Tenure"] =((Material_Master['current'] - Material_Master['FIRST SALES WEEK']).dt.days/7)+1
Material_Master["Material_Ageing_Tenure"] =((Material_Master['current'] - Material_Master['FIRST AGEING WEEK']).dt.days/7)+1
Material_Master = Material_Master.drop(['current'], axis=1)
bins=[-1,0,4,8,12,16,24,36,48,60,96,144]
Material_Master["Sales_Tenure_bands"] = pd.cut(Material_Master['Material_Sales_Tenure'], bins=bins)
Material_Master["Ageing_Tenure_bands"] = pd.cut(Material_Master['Material_Ageing_Tenure'], bins=bins)

##JOINING R-ELAN FLAGS WITH MATERIAL MASTERS AND CLASSIFICATION OF ELIGIBLE REGULAR MERGES


Material_Master_1=pd.merge(Material_Master,d_l_df[["MATERIAL","Lustre","DENIER"]],how="left",on=["MATERIAL"])
new = ["PFSDAM--","PFSDGRN-","PFSDSLOP","PFSDH---","GRN"]
def total(r):
        if "GRN" in str(r["Lustre"]):
            return 1
        if r["Lustre"] in ["PFSDAM--","PFSDSLOP","PFSDH---","PFBKHF--","PFBKHGR-","PFMTBS--","PFSDEG--","PFSDSLGR","PFBRGTR-","PFBRFR--"]:
            return 1
        else:
            return 0
          
Material_Master_1['R_ELAN_FLAG'] = Material_Master_1.apply(total, axis=1)
Material_Master_1["No. OF AGEING WEEKS"]=Material_Master_1["No. OF AGEING WEEKS"].fillna(0)
Material_Master_1["SALES WEEK COUNT"]=Material_Master_1["SALES WEEK COUNT"].fillna(0)
Regular_Merges=Material_Master_1.loc[(Material_Master_1["R_ELAN_FLAG"]==0) & (Material_Master_1["No. OF AGEING WEEKS"]!=0) & (Material_Master_1["SALES WEEK COUNT"]!=0)]

                                       
                                
                                       











In [8]:
Material_Master_1.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Material_master_feb_thrs_400kg.csv")
Regular_Merges

MATERIAL  PRODUCTION QUANTITY  NO OF PRODUCTION WEEK  \
0        A06G20               8.5492                    5.0   
1        A06G21              10.9200                    3.0   
2        A06G22              26.4262                    6.0   
9       A10TP19              33.3600                    4.0   
10      A10TP20              15.9384                    2.0   
...         ...                  ...                    ...   
1226  SPB4QT5T1                  NaN                    NaN   
1227     TB6Y10                  NaN                    NaN   
1264     Z0PW25                  NaN                    NaN   
1266      Z4F70                  NaN                    NaN   
1267      Z4L70                  NaN                    NaN   

      PRODUCTION QUANTITY PER WEEK FIRST SALES WEEK LAST SALES WEEK  \
0                         1.709840       2017-07-24      2018-07-09   
1                         3.640000       2017-11-13      2018-06-25   
2                         4.404367       2017-07-31      2019-07-15   
9                         8.340000       2017-12-11      2020-12-07   
10                        7.969200       2018-09-17      2020-02-17   
...                            ...              ...             ...   
1226                           NaN       2018-01-15      2018-04-30   
1227                           NaN       2018-04-09      2018-04-09   
1264                           NaN       2017-07-17      2017-09-25   
1266                           NaN       2020-11-23      2021-05-17   
1267                           NaN       2020-09-28      2021-05-17   

      SALES WEEK COUNT  TOTAL WEEKS  TOTAL SALES QUANTITY  \
0                  8.0         51.0                 8.888   
1                 10.0         33.0                11.611   
2                 12.0        103.0                29.319   
9                 10.0        157.0                33.620   
10                 4.0         75.0                15.939   
...                ...          ...                   ...   
1226               3.0         16.0                19.103   
1227               1.0          1.0                 2.565   
1264               4.0         11.0                20.623   
1266               8.0         26.0                47.129   
1267               6.0         34.0                21.550   

      SALES TRANSACTION COUNT  ...  FIRST AGEING WEEK  LAST AGEING WEEK  \
0                        10.0  ...         2017-07-24        2018-09-03   
1                        11.0  ...         2017-07-24        2018-03-26   
2                        16.0  ...         2017-07-24        2019-04-29   
9                        12.0  ...         2018-01-08        2020-03-09   
10                        5.0  ...         2018-11-19        2020-02-10   
...                       ...  ...                ...               ...   
1226                      4.0  ...         2018-03-12        2018-04-23   
1227                      1.0  ...         2017-07-10        2018-04-02   
1264                      4.0  ...         2017-07-10        2017-09-25   
1266                      9.0  ...         2020-08-10        2020-10-12   
1267                     12.0  ...         2020-08-10        2020-10-12   

      AGEING RATIO_%  Material_Sales_Tenure  Material_Ageing_Tenure  \
0          16.949153                  206.0                   206.0   
1          52.777778                  190.0                   206.0   
2          17.204301                  205.0                   206.0   
9          21.052632                  186.0                   182.0   
10         23.076923                  146.0                   137.0   
...              ...                    ...                     ...   
1226      100.000000                  181.0                   173.0   
1227      100.000000                  169.0                   208.0   
1264      100.000000                  207.0                   208.0   
1266      100.000000                   32.0          

In [9]:
##PREPRATION OF EVERY WEEK DATA

prod_nonzero_data=Production_aggregation.copy()
sales_nonzero_data=sales_aggregation.copy()
ageing_nonzero_data=Ageing_aggregation.copy()
prod_nonzero_data=prod_nonzero_data.drop(["Material Description"],axis=1)

sales_columns=["Monday_Dates","Material Code","Total Quantity","Transaction Count","Total Quantity,Transaction Count","Region_Count",
               "Unique_Sales_Plant_Count","COUNT_DEPOT(EXCISE)","COUNT_EXPORT PORT","COUNT_LOGICAL PLANT","COUNT_PRODUCTION PLANT",
               "SALES_DEPOT(EXCISE)","SALES_EXPORT PORT","SALES_LOGICAL PLANT","SALES_PRODUCTION PLANT","COUNT_EXP",
               "COUNT_N002","COUNT_N006","COUNT_S003","COUNT_S005","COUNT_W006","SALES_EXP","SALES_N002","SALES_N006",
               "SALES_S003","SALES_S005","SALES_W006"]
prod_nonzero_data=prod_nonzero_data.rename(columns={"Material":"Material Code","WEEKDAY":"Monday_Dates"})
sales_nonzero_data.columns=sales_columns
initial_date='2017-07-03'
test_date='2020-03-30'

material =Regular_Merges["MATERIAL"].tolist()### insert ELIGIBLE REGULAR materials to this list


idx_old = pd.date_range(initial_date,test_date,freq = 'W-MON')##contains all weekly dates
idx_new = pd.date_range(start_date,end_date,freq = 'W-MON')
idx=idx_old.union(idx_new)
#print(idx)
prod_every_week=pd.DataFrame()
sales_every_week=pd.DataFrame()
ageing_every_week=pd.DataFrame()


for value in material:
    data_prod = pd.DataFrame(columns =prod_nonzero_data.columns)
    data_sales = pd.DataFrame(columns =sales_nonzero_data.columns)
    data_ageing = pd.DataFrame(columns =ageing_nonzero_data.columns)
    for i in idx:
        dat = str(i).split(' ')[0]
        data_prod = data_prod.append({'Monday_Dates':dat, 'Material Code':value, 'TOTAL PRODUCTION':0,'NUMBER OF PALLETS':0, 'COUNT OF TRANSACTIONS':0},ignore_index=True)
    for i in idx:
        dat = str(i).split(' ')[0]
        data_sales = data_sales.append({'Monday_Dates':dat, 'Material Code':value, 'Total Quantity':0, 'Transaction Count':0,
                                        'Total Quantity,Transaction Count':0, 'Region_Count':0,
                                        'Unique_Sales_Plant_Count':0, 'COUNT_DEPOT(EXCISE)':0, 'COUNT_EXPORT PORT':0,
                                       'COUNT_LOGICAL PLANT':0, 'COUNT_PRODUCTION PLANT':0, 'SALES_DEPOT(EXCISE)':0,
                                       'SALES_EXPORT PORT':0, 'SALES_LOGICAL PLANT':0, 'SALES_PRODUCTION PLANT':0,
                                       'COUNT_EXP':0, 'COUNT_N002':0, 'COUNT_N006':0, 'COUNT_S003':0, 'COUNT_S005':0,
                                       'COUNT_W006':0, 'SALES_EXP':0, 'SALES_N002':0, 'SALES_N006':0, 'SALES_S003':0,
                                       'SALES_S005':0, 'SALES_W006':0},ignore_index=True)
    for i in idx:
        dat = str(i).split(' ')[0]
        data_ageing = data_ageing.append({'WEEKDAY':dat, 'MATERIAL':value, 'TOTAL STOCK':0, '0-15 DAYS':0, '16-30 DAYS':0,
                                           '31-46 DAYS':0, '46-60 DAYS':0, '61-90 DAYS':0, '91-150 DAYS':0, '150-180 DAYS':0,
                                           '>365 DAYS':0, 'AGED STOCK':0, 'AGEING FLAG':0},ignore_index=True)
    
    data_prod['Monday_Dates'] = pd.to_datetime(data_prod['Monday_Dates'])
    data_sales['Monday_Dates'] = pd.to_datetime(data_sales['Monday_Dates'])
    data_ageing['WEEKDAY'] = pd.to_datetime(data_ageing['WEEKDAY'])
    
    prod_nonzero = prod_nonzero_data[prod_nonzero_data['Material Code']==value]
    sales_nonzero = sales_nonzero_data[sales_nonzero_data['Material Code']==value]
    ageing_nonzero = ageing_nonzero_data[ageing_nonzero_data['MATERIAL']==value]
    
    df_prod = pd.concat([data_prod,prod_nonzero]).drop_duplicates(['Monday_Dates','Material Code'],keep='last')
    df_sales = pd.concat([data_sales,sales_nonzero]).drop_duplicates(['Monday_Dates','Material Code'],keep='last')
    df_ageing = pd.concat([data_ageing,ageing_nonzero]).drop_duplicates(['WEEKDAY','MATERIAL'],keep='last')
    
    prod_every_week=pd.concat([prod_every_week,df_prod])
    sales_every_week=pd.concat([sales_every_week,df_sales])
    ageing_every_week=pd.concat([ageing_every_week,df_ageing])
    
sales_and_prod=pd.merge(sales_every_week,prod_every_week[prod_every_week.columns],how='outer',on=['Monday_Dates','Material Code'])
sales_and_prod["Next Week"]=sales_and_prod["Monday_Dates"]+timedelta(days=7)



/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:61: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



In [10]:
##MODEL VARIABLES CREATION

df = ageing_every_week.copy() 
df=df.reset_index(drop=True)
df["WEEKDAY"]=pd.to_datetime(df["WEEKDAY"])
#df["AGED_STOCK_30"]=df["TOTAL STOCK"]-(df["0-15 DAYS"]+df["16-30 DAYS"])
#df['AGEING_FLAG_30'] = df['AGED_STOCK_30'].apply(lambda x: "YES" if x > 1 else "NO")
df=df.rename(columns={'WEEKDAY':"Next Week",'MATERIAL':'Material Code'})
df["AGED STOCK"]=df["AGED STOCK"].apply(lambda x: 0 if x < 1 else x )/1000
df["Monday_Dates"]=df["Next Week"]
df["AGEING FLAG"]=df["AGEING FLAG"].apply(lambda x:"NO" if x==0 else x)
df=df.sort_values(by=['Next Week'])
x = df.groupby('Material Code')['AGED STOCK'].rolling(4).sum().apply(lambda x: 0 if x < 1e-9 else x)
df["LAST_4_WEEK_AGED_STOCK"] = x.reset_index(level=0, drop=True)
y = df.groupby('Material Code')['AGED STOCK'].rolling(12).sum().apply(lambda x: 0 if x < 1e-9 else x)
df["LAST_12_WEEK_AGED_STOCK"] = y.reset_index(level=0, drop=True)
z = df.groupby('Material Code')['AGED STOCK'].rolling(24).sum().apply(lambda x: 0 if x < 1e-9 else x)
df["LAST_24_WEEK_AGED_STOCK"] = z.reset_index(level=0, drop=True)
df.LAST_4_WEEK_AGED_STOCK.fillna(df['AGED STOCK'],inplace = True)
df.LAST_12_WEEK_AGED_STOCK.fillna(df['AGED STOCK'],inplace = True)
df.LAST_24_WEEK_AGED_STOCK.fillna(df['AGED STOCK'],inplace = True)
df['AGEING_FLAG_31_46'] = df['31-46 DAYS'].apply(lambda x: "YES" if x > 1 else "NO")
df['AGEING_FLAG_46_60'] = df['46-60 DAYS'].apply(lambda x: "YES" if x > 1 else "NO")
#f["AGEING FLAG"].value_counts()

##SALES AND PRODUCTION
df1 = sales_and_prod.copy()
df=df.reset_index(drop=True)
df1=df1.rename(columns={"Total Quantity,Transaction Count":"Count_of_unique_group_code"})
df1["Monday_Dates"]=pd.to_datetime(df1['Monday_Dates'])
df1["Next Week"]=pd.to_datetime(df1['Next Week'])

df1=df1.sort_values(by=['Monday_Dates'])
x = df1.groupby('Material Code')['Total Quantity'].rolling(4).sum().apply(lambda x: 0 if x < 1e-9 else x)
df1["LAST_4_WEEK_SALES"] = x.reset_index(level=0, drop=True)
y = df1.groupby('Material Code')['Total Quantity'].rolling(12).sum().apply(lambda x: 0 if x < 1e-9 else x)
df1["LAST_12_WEEK_SALES"] = y.reset_index(level=0, drop=True)
z = df1.groupby('Material Code')['Total Quantity'].rolling(24).sum().apply(lambda x: 0 if x < 1e-9 else x)
df1["LAST_24_WEEK_SALES"] = z.reset_index(level=0, drop=True)
df1.LAST_4_WEEK_SALES.fillna(df1['Total Quantity'],inplace = True)
df1.LAST_12_WEEK_SALES.fillna(df1['Total Quantity'],inplace = True)
df1.LAST_24_WEEK_SALES.fillna(df1['Total Quantity'],inplace = True)

##AVERAGE SALES

df1["LAST_4_WEEK_AVG_SALES"]=df1["LAST_4_WEEK_SALES"]/4
df1["LAST_12_WEEK_AVG_SALES"]=df1["LAST_12_WEEK_SALES"]/12
df1["LAST_24_WEEK_AVG_SALES"]=df1["LAST_24_WEEK_SALES"]/24
Model_var_temp=pd.merge(df1,df[["Material Code","Monday_Dates","AGED STOCK","AGEING FLAG","LAST_4_WEEK_AGED_STOCK","LAST_12_WEEK_AGED_STOCK","LAST_24_WEEK_AGED_STOCK","AGEING_FLAG_31_46","AGEING_FLAG_46_60"]],how='left',on=["Material Code","Monday_Dates"])
#Model_var_temp=pd.merge(df1,df[["Material Code","Next Week","AGED STOCK","AGEING FLAG","LAST_4_WEEK_AGED_STOCK","LAST_12_WEEK_AGED_STOCK","LAST_24_WEEK_AGED_STOCK"]],how='left',on=["Material Code","Next Week"])
Model_var_temp=Model_var_temp.rename(columns={'AGEING FLAG':"AGEING_FLAG_CURRENT"})
Model_var=pd.merge(Model_var_temp,df[["Material Code","Next Week","AGEING FLAG"]],how='left',on=["Material Code","Next Week"])

#Model_var['Monday_Dates'] = pd.to_datetime(Model_var['Monday_Dates'])
#Model_var["Next Week"]=pd.to_datetime(Model_var["Next Week"])
Model_var=Model_var.sort_values(by=['Monday_Dates'])
Model_var['AGEING FLAG'] = Model_var['AGEING FLAG'].eq('YES').mul(1)
Model_var['AGEING_FLAG_31_46'] = Model_var['AGEING_FLAG_31_46'].eq('YES').mul(1)
Model_var['AGEING_FLAG_46_60'] = Model_var['AGEING_FLAG_46_60'].eq('YES').mul(1)
Model_var['AGEING_FLAG_CURRENT'] = Model_var['AGEING_FLAG_CURRENT'].eq('YES').mul(1)
x = Model_var.groupby('Material Code')['AGEING_FLAG_CURRENT'].rolling(4).sum()

Model_var["LAST_4_AGEING_WEEK_COUNT"] = x.reset_index(level=0, drop=True)
Model_var.LAST_4_AGEING_WEEK_COUNT.fillna(Model_var['AGEING_FLAG_CURRENT'],inplace = True)
y = Model_var.groupby('Material Code')['AGEING_FLAG_CURRENT'].rolling(12).sum()
Model_var["LAST_12_AGEING_WEEK_COUNT"] = y.reset_index(level=0, drop=True)
Model_var.LAST_12_AGEING_WEEK_COUNT.fillna(Model_var['AGEING_FLAG_CURRENT'],inplace = True)
try:
    Model_var["Sales_Quantity_Per_Transaction"]=Model_var["Total Quantity"]/Model_var["Transaction Count"]
    Model_var["Poduction_Quantity_Per_Transaction"]=Model_var["TOTAL PRODUCTION"]/Model_var["COUNT OF TRANSACTIONS"]
except ZeroDivisionError:
    Model_var["Sales_Quantity_Per_Transaction"]=0
    Model_var["Poduction_Quantity_Per_Transaction"]=0

Model_var["AGED_STOCK_BY_SALES_4_WEEKS"]=Model_var["LAST_4_WEEK_AGED_STOCK"]/Model_var["LAST_4_WEEK_SALES"]
Model_var["AGED_STOCK_BY_SALES_12_WEEKS"]=Model_var["LAST_12_WEEK_AGED_STOCK"]/Model_var["LAST_12_WEEK_SALES"]
Model_var["AGED_STOCK_BY_SALES_24_WEEKS"]=Model_var["LAST_24_WEEK_AGED_STOCK"]/Model_var["LAST_24_WEEK_SALES"]



#Model_var = Model_var.replace([np.inf, -np.inf], np.nan)


Model_var.LAST_4_WEEK_AGED_STOCK.fillna(0,inplace = True)
Model_var.LAST_12_WEEK_AGED_STOCK.fillna(0,inplace = True)
Model_var.LAST_24_WEEK_AGED_STOCK.fillna(0,inplace = True)


#Model_var['AGEING_FLAG_3%_Sales'] = np.where(( (Model_var['AGED STOCK'] > Model_var['Total Quantity']*0.03) or (Model_var['AGED STOCK']>3000 )), 1, 0)

Model_var.AGED_STOCK_BY_SALES_4_WEEKS.fillna(Model_var['LAST_4_WEEK_AGED_STOCK'],inplace = True)
Model_var.AGED_STOCK_BY_SALES_12_WEEKS.fillna(Model_var['LAST_12_WEEK_AGED_STOCK'],inplace = True)
Model_var.AGED_STOCK_BY_SALES_24_WEEKS.fillna(Model_var['LAST_12_WEEK_AGED_STOCK'],inplace = True)

Model_var['AGED_STOCK_BY_SALES_4_WEEKS'] = np.where(Model_var.LAST_4_WEEK_SALES == 0,Model_var.LAST_4_WEEK_AGED_STOCK, Model_var.AGED_STOCK_BY_SALES_4_WEEKS)
Model_var['AGED_STOCK_BY_SALES_12_WEEKS'] = np.where(Model_var.LAST_12_WEEK_SALES == 0,Model_var.LAST_12_WEEK_AGED_STOCK, Model_var.AGED_STOCK_BY_SALES_12_WEEKS)
Model_var['AGED_STOCK_BY_SALES_24_WEEKS'] = np.where(Model_var.LAST_24_WEEK_SALES == 0,Model_var.LAST_24_WEEK_AGED_STOCK, Model_var.AGED_STOCK_BY_SALES_24_WEEKS)

df = Model_var[['Material Code', 'Monday_Dates', 'Total Quantity', 'TOTAL PRODUCTION']]

def calc_slope(x):
    slope = np.polyfit(range(len(x)), x, 1)[0]
    return slope
df_ss = df[['Material Code', 'Monday_Dates', 'Total Quantity']]
df_ss['sales_trend_4w'] = None
df_ss['sales_trend_12w'] = None

df_ms = pd.DataFrame(columns=df_ss.columns)

for i in df_ss['Material Code'].unique() :
    
    df_s = df_ss[df_ss['Material Code']==i].sort_values('Monday_Dates')
    
    df_s['sales_trend_4w'] = df_s['Total Quantity'].rolling(4).apply(calc_slope)
    df_s['sales_trend_12w'] = df_s['Total Quantity'].rolling(12).apply(calc_slope)
    
    df_ms = df_ms.append(df_s)

df_pp = df[['Material Code', 'Monday_Dates', 'TOTAL PRODUCTION']]
df_pp['prod_trend_4w'] = None
df_pp['prod_trend_12w'] = None

df_mp = pd.DataFrame(columns=df_pp.columns)

for i in df_pp['Material Code'].unique() :
    
    df_p = df_pp[df_pp['Material Code']==i].sort_values('Monday_Dates')
    
    df_p['prod_trend_4w'] = df_p['TOTAL PRODUCTION'].rolling(4).apply(calc_slope)
    df_p['prod_trend_12w'] = df_p['TOTAL PRODUCTION'].rolling(12).apply(calc_slope)
    
    df_mp = df_mp.append(df_p)

a=pd.merge(df_ms,df_mp,on=['Material Code', 'Monday_Dates'], how='outer' )
a=a.drop(["Total Quantity","TOTAL PRODUCTION"],axis=1)
var=pd.merge(Model_var,a,on=['Material Code', 'Monday_Dates'], how='inner')

crude_data['Monday_Dates']=pd.to_datetime(crude_data["Monday_Dates"])

var_new=pd.merge(var,crude_data,on=['Monday_Dates'], how='inner')
var_new=var_new.rename(columns={'AGEING FLAG':"AGEING_FLAG_GT_60"})





/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:114: FutureWarning: Currently, 'apply' passes the values as ndarrays to the applied function. In the future, this will change to passing it as Series objects. You need to specify 'raw=True' to keep the current behaviour, and you can pass 'raw=False' to silence this warning
/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:115: FutureWarning: Currently, 'apply' passes the values as ndarrays to the applied function. In the future, this will change to passing it as Series objects. You need to specify 'raw=True' to keep the current behaviour, and you can pass 'raw=False' to silence this warning
/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:129: FutureWarning: Currently, 'apply' passes the values as ndarrays to the applied function. In the future, this will change to passing it as Series objects. You need to specify 'raw=True' to keep the current behaviour, and you can pass 'raw=False' to silence this war

In [11]:
##MODELLING AUTOMATION FOR ALL FIVE MODELS
cols=[i for i in var_new.columns if i not in ["Monday_Dates","Material Code","Next Week"]]
for col in cols:
   # print(col)
    var_new[col]=var_new[col].astype(float)

var_new_df=var_new.copy()
var_new_1=var_new_df.drop(["AGED STOCK","NUMBER OF PALLETS"],axis=1)
#print(var_new_1.info())
var_new_1['Ageing_lead_1_Flag'] = (var_new_1.sort_values(by=['Monday_Dates'], ascending=True)
                       .groupby(['Material Code'])['AGEING_FLAG_CURRENT'].shift(-1))
var_new_1['Ageing_lead_2_Flag'] = (var_new_1.sort_values(by=['Monday_Dates'], ascending=True)
                       .groupby(['Material Code'])['AGEING_FLAG_CURRENT'].shift(-2))
var_new_1['Ageing_lead_3_Flag'] = (var_new_1.sort_values(by=['Monday_Dates'], ascending=True)
                       .groupby(['Material Code'])['AGEING_FLAG_CURRENT'].shift(-3))

var_new_1['Ageing_lead_4_Flag'] = (var_new_1.sort_values(by=['Monday_Dates'], ascending=True)
                       .groupby(['Material Code'])['AGEING_FLAG_CURRENT'].shift(-4))

var_new_1['Ageing_lead_8_Flag'] = (var_new_1.sort_values(by=['Monday_Dates'], ascending=True)
                       .groupby(['Material Code'])['AGEING_FLAG_CURRENT'].shift(-8))

def Model_Output(material,target):
    #Data Cleaning
    merge=material
    data=var_new_1.loc[var_new_1["Material Code"]==merge]

    data["Sales_Quantity_Per_Transaction"]=data["Sales_Quantity_Per_Transaction"].fillna(0)
    data["Poduction_Quantity_Per_Transaction"]=data["Poduction_Quantity_Per_Transaction"].fillna(0)
    data["sales_trend_4w"]=data["sales_trend_4w"].fillna(0)
    data["sales_trend_12w"]=data["sales_trend_12w"].fillna(0)
    data["prod_trend_4w"]=data["prod_trend_4w"].fillna(0)
    data["prod_trend_12w"]=data["prod_trend_12w"].fillna(0)
    data_full=data.copy()
    data = data[data[target].notna()]
    data=data.loc[data["Monday_Dates"]<=train_stop_date]
    data_predic=data_full.loc[data_full["Monday_Dates"]>=train_stop_date]
    #print(data)
   
    #Selection of variables relevant for modelling-Manual Selection
    var_list=["Total Quantity","Transaction Count","Count_of_unique_group_code","Region_Count","Unique_Sales_Plant_Count",
          "TOTAL PRODUCTION","COUNT OF TRANSACTIONS","LAST_4_WEEK_SALES","LAST_12_WEEK_SALES",'LAST_24_WEEK_SALES', 'LAST_24_WEEK_AVG_SALES',
          "LAST_4_WEEK_AVG_SALES","LAST_12_WEEK_AVG_SALES","AGEING_FLAG_31_46","AGEING_FLAG_46_60","LAST_4_AGEING_WEEK_COUNT",
        "LAST_12_AGEING_WEEK_COUNT","Sales_Quantity_Per_Transaction","Poduction_Quantity_Per_Transaction",
          "sales_trend_4w","sales_trend_12w","prod_trend_4w","prod_trend_12w","Avg PSF Price (Rs/Kg)",
          "Avg Cotton Price (Rs/Candy)","Avg of Crude_Price",target,'AGED_STOCK_BY_SALES_4_WEEKS', 
          'AGED_STOCK_BY_SALES_12_WEEKS','AGED_STOCK_BY_SALES_24_WEEKS']
   
    #Splitting data into target variables and training features
    df=data[var_list]
    numerical_feature_columns = list(df._get_numeric_data().columns)
    df=df.loc[:, (df != 0).any(axis=0)]
    
    X = df.loc[:, df.columns != target]
    Y = df.loc[:, df.columns == target]
    
    
    
    #This function will remove Multi-Colinearity-VIF Elimination in a Recursive mannner
    def calculate_vif_(X, thresh=15):
        variables = list(range(X.shape[1]))
        dropped = True
        while dropped:
            dropped = False
            vif = [variance_inflation_factor(X.iloc[:, variables].values, ix)
                   for ix in range(X.iloc[:, variables].shape[1])]

            maxloc = vif.index(max(vif))

            if max(vif) > thresh:
                
                del variables[maxloc]
                dropped = True
                
        return  X.iloc[:, variables].columns,vif
        
    
        
    variables_ls,vif_value=calculate_vif_(X)    # List of variables after VIF elimination
    
    ## Checking for highly co-related variables and keeping only variable
    corr=X[variables_ls].corr()
    columns = np.full((corr.shape[0],), True, dtype=bool)
    for i in range(corr.shape[0]):
        for j in range(i+1, corr.shape[0]):
            if corr.iloc[i,j] > 0.95:
                if columns[j]:
                    columns[j] = False
    selected_columns = X[variables_ls].columns[columns]    #List of variables after checking high co-relation
    
   
    #Splitting into Training and Test Data Set
    x_train, x_test, y_train, y_test = train_test_split(X, Y, stratify=Y,  
                                                test_size=0.15, random_state=5)
    
    #More Data filteration to tackle singular matrix error i.e removal of features having zeroes more than 50%
    binary_list=[]
    if "AGEING_FLAG_31_46" in selected_columns:
        binary_list.append("AGEING_FLAG_31_46")
    if "AGEING_FLAG_46_60" in selected_columns:
        binary_list.append("AGEING_FLAG_46_60")
    
        
    list_filtered_bin=[j for j in binary_list if x_train[j].sum()>=11 and x_train[j].sum()<=104]
    
    list_filtered=list(set(selected_columns) - set(binary_list))
    
    
    
    list_filtered_1=[i for i in list_filtered if x_train[i].quantile(0.5)==0]
    
    final_var_temp=list(set(list_filtered) - set(list_filtered_1))
    
    final_var=list_filtered_bin + final_var_temp      #List of variables eligible for Logit Convergence
    
    #This function will return stastical summary of significant variable and their list after doing significance test in recurssive manner
    
    def backwardElimination(x, Y, sl, columns):
            numVars = len(x[0])
            for i in range(0, numVars):
                regressor_OLS = sm.Logit(Y, x).fit()
                maxVar = max(regressor_OLS.pvalues)
                if maxVar > sl:
                    for j in range(0, numVars - i):
                        if (regressor_OLS.pvalues[j] == maxVar):
                            x = np.delete(x, j, 1)
                            columns = np.delete(columns, j)

            results_summary=regressor_OLS.summary()
            results_as_html = results_summary.tables[1].as_html()
            significant_df=pd.read_html(results_as_html, header=0, index_col=0)[0]
            significant_df["Variables"]=columns
            
            
            return significant_df, columns
    SL = 0.15
    significant_df1, selected_columns_last = backwardElimination(x_train[final_var].values, y_train[target].values, SL, final_var)  #Returns Summary Data Frame and list of significant variables
    significant_df1["Material_Code"]=merge
    
    #Logistic Regression Model- Scikit Learn

    clf_lr = LogisticRegression()      
    lr_baseline_model = clf_lr.fit(x_train[selected_columns_last],y_train) #Training model using list of significant variables from Logit
    #Evaluation on Training Data
    ac = accuracy_score(y_train,lr_baseline_model.predict(x_train[selected_columns_last]))
#     f_score_ac = f1_score(y_train,lr_baseline_model.predict(x_train[selected_columns_last]),average="weighted") # Weighted average of HM of Precision & Recall
#     f_score_train_0 = f1_score(y_train,lr_baseline_model.predict(x_train[selected_columns_last]),pos_label=0)
#     f_score_train_1 = f1_score(y_train,lr_baseline_model.predict(x_train[selected_columns_last]),pos_label=1)
    cm = confusion_matrix(y_train,lr_baseline_model.predict(x_train[selected_columns_last]))
    f1_score_train=f1_score(y_train,lr_baseline_model.predict(x_train[selected_columns_last]))
    recall_train=recall_score(y_train,lr_baseline_model.predict(x_train[selected_columns_last]))
    precision_train=precision_score(y_train,lr_baseline_model.predict(x_train[selected_columns_last]))
    f2_train=fbeta_score(y_train,lr_baseline_model.predict(x_train[selected_columns_last]),beta=2)
#     print(cm)
#     print(f1_score_train)
#     print(recall_train)
#    auc_train = roc_auc_score(y_train, lr_baseline_model.predict_proba(x_train[selected_columns_last])[:,1])
    
    
    #Evaluation robustness on Unseen Data

    robustnes = accuracy_score(y_test,lr_baseline_model.predict(x_test[selected_columns_last]))
#     f_score_rob = f1_score(y_test,lr_baseline_model.predict(x_test[selected_columns_last]),average="weighted") # Weighted average of HM of Precision & Recall
#     f_score_test_0 = f1_score(y_test,lr_baseline_model.predict(x_test[selected_columns_last]),pos_label=0)
#     f_score_test_1 = f1_score(y_test,lr_baseline_model.predict(x_test[selected_columns_last]),pos_label=1)
    cm_rob = confusion_matrix(y_test,lr_baseline_model.predict(x_test[selected_columns_last]))
    f1_score_test = f1_score(y_test,lr_baseline_model.predict(x_test[selected_columns_last]))
    recall_test=recall_score(y_test,lr_baseline_model.predict(x_test[selected_columns_last]))
    precision_test=precision_score(y_test,lr_baseline_model.predict(x_test[selected_columns_last]))
    f2_test=fbeta_score(y_test,lr_baseline_model.predict(x_test[selected_columns_last]),beta=2)
    print(cm_rob)
#     print(f1_score_test)
#     print(recall_test)
    
#    auc_test = roc_auc_score(y_test, lr_baseline_model.predict_proba(x_test[selected_columns_last])[:,1])
    
    
    #Obtaining Probabilities and flag corresponding to all data points
    pred_data=pd.DataFrame(data_predic).reset_index()
    pred_prob_df=pd.DataFrame(lr_baseline_model.predict_proba(data_predic[selected_columns_last]),columns=["PREDICTED_NON_AGEING_PROBABILITY","PREDICTED_AGEING_PROBABILITY"])
    pred_df=pd.DataFrame(lr_baseline_model.predict(data_predic[selected_columns_last]),columns=["PREDICTED_FLAG"])
    Prob_df=pd.concat([pred_data,pred_prob_df,pred_df],axis=1)  #Concatination of three Data Frame
    
    #Beta cofficients and odds ratios from Logistic Regression
    log_coefficients = pd.concat([pd.DataFrame(x_train[selected_columns_last].columns,columns=["Variables"]).reset_index(),pd.DataFrame(np.transpose(clf_lr.coef_),columns=["Beta_Values"])], axis = 1)
    log_coefficients["Material"]=merge
    
    #Creation of Performance Evaluation matrix
    Model_output_df=pd.DataFrame({"Material_Code":[merge],
                             "Accuracy_Score":[ac],
                            "F1_Score_train":[f1_score_train],
                                "Recall_Train":[recall_train],
                                  "Robustness":[robustnes],
                                  "F1_score_test":[f1_score_test],
                                  "Recall_Test":[recall_test],
                                  "Precision_train":[precision_train],
                                  "Precision_test":[precision_test],
                                  "F2_score_train":[f2_train],
                                  "F2_score_test":[f2_test]
                                  
                                  })
    
    #Creation of datafrme for stastical summary of significant variables
    summary_df=pd.DataFrame()
    
    for var in selected_columns_last:
        
        temp_df=pd.DataFrame()
        group=df.groupby([target])
        temp_df["Average"+" "+ var]=group[var].mean()
        
        summary_df = pd.concat([summary_df, temp_df], axis=1)
    summary_df["MATERIAL_CODE"]=merge
        
    
    
        
    
    
    return Model_output_df,significant_df1,summary_df,log_coefficients,Prob_df  #Return Evaluation , significant variables, stastical summary, Beta cofficients, Proabilities dataframe
    
        







In [12]:
material_list=Regular_Merges["MATERIAL"].tolist()
final_material_list_1=[]
final_material_list_2=[]
final_material_list_3=[]
final_material_list_4=[]
#final_material_list_8=[]
for m in material_list:
    merge_df=var_new_1.loc[var_new["Material Code"]==m]
    count_1=merge_df["Ageing_lead_1_Flag"].sum()
    count_2=merge_df["Ageing_lead_2_Flag"].sum()
    count_3=merge_df["Ageing_lead_3_Flag"].sum()
    count_4=merge_df["Ageing_lead_4_Flag"].sum()
    #count_8=merge_df["Ageing_lead_8_Flag"].sum()
    if count_1>=0.05*(len(idx)-1) and count_1<=0.95*(len(idx)-1):
        final_material_list_1.append(m)
    if count_2>=0.05*(len(idx)-2) and count_2<=0.95*(len(idx)-2):
        final_material_list_2.append(m)
    if count_3>=0.05*(len(idx)-3) and count_3<=0.95*(len(idx)-3):
        final_material_list_3.append(m)
    if count_4>=0.05*(len(idx)-4) and count_4<=0.95*(len(idx)-4):
        final_material_list_4.append(m)
    #if count_8>=7 and count_8<=129:
    #    final_material_list_8.append(m) #List of eligible merges



In [13]:
class_imb_df_1=pd.DataFrame({"Material_Code":list(set(material_list) - set(final_material_list_1))})
class_imb_df_2=pd.DataFrame({"Material_Code":list(set(material_list) - set(final_material_list_2))})
class_imb_df_3=pd.DataFrame({"Material_Code":list(set(material_list) - set(final_material_list_3))})
class_imb_df_4=pd.DataFrame({"Material_Code":list(set(material_list) - set(final_material_list_4))})




In [14]:
#Run for all the Merges
#W+1
Master_Score_df_1=pd.DataFrame()
Master_Variables_df_1=pd.DataFrame()
Master_Summary_df_1=pd.DataFrame()
Master_Beta_df_1=pd.DataFrame()
Master_prob_df_1=pd.DataFrame()
error_list_1=[]
flag_1="Ageing_lead_1_Flag"
#W+2 
Master_Score_df_2=pd.DataFrame()
Master_Variables_df_2=pd.DataFrame()
Master_Summary_df_2=pd.DataFrame()
Master_Beta_df_2=pd.DataFrame()
Master_prob_df_2=pd.DataFrame()
error_list_2=[]
flag_2="Ageing_lead_2_Flag"
#W+3
Master_Score_df_3=pd.DataFrame()
Master_Variables_df_3=pd.DataFrame()
Master_Summary_df_3=pd.DataFrame()
Master_Beta_df_3=pd.DataFrame()
Master_prob_df_3=pd.DataFrame()
error_list_3=[]
flag_3="Ageing_lead_3_Flag"
#W+4
Master_Score_df_4=pd.DataFrame()
Master_Variables_df_4=pd.DataFrame()
Master_Summary_df_4=pd.DataFrame()
Master_Beta_df_4=pd.DataFrame()
Master_prob_df_4=pd.DataFrame()
error_list_4=[]
flag_4="Ageing_lead_4_Flag"
#W+8
# Master_Score_df_8=pd.DataFrame()
# Master_Variables_df_8=pd.DataFrame()
# Master_Summary_df_8=pd.DataFrame()
# Master_Beta_df_8=pd.DataFrame()
# Master_prob_df_8=pd.DataFrame()
# error_list_8=[]
# flag_8="Ageing_lead_8_Flag"

#W+1(model run)
for material in final_material_list_1:
    
    try:
        score_df_1,variables_df_1,summ_df_1,beta_df_1,Probability_df_1=Model_Output(material,flag_1) #Function will be called to train model
        Master_Score_df_1=pd.concat([Master_Score_df_1,score_df_1])
        Master_Variables_df_1=pd.concat([Master_Variables_df_1,variables_df_1])
        Master_Summary_df_1 = Master_Summary_df_1.append(summ_df_1)
        Master_Beta_df_1=pd.concat([Master_Beta_df_1,beta_df_1])
        Master_prob_df_1=pd.concat([Master_prob_df_1,Probability_df_1])
    except:
        error_list_1.append(material)      #list of Merges for exception came
        
#W+2        

for material in final_material_list_2:
    
    try:
        score_df_2,variables_df_2,summ_df_2,beta_df_2,Probability_df_2=Model_Output(material,flag_2) #Function will be called to train model
        Master_Score_df_2=pd.concat([Master_Score_df_2,score_df_2])
        Master_Variables_df_2=pd.concat([Master_Variables_df_2,variables_df_2])
        Master_Summary_df_2 = Master_Summary_df_2.append(summ_df_2)
        Master_Beta_df_2=pd.concat([Master_Beta_df_2,beta_df_2])
        Master_prob_df_2=pd.concat([Master_prob_df_2,Probability_df_2])
    except:
        error_list_2.append(material)      #list of Merges for exception came
        
#W+3       

for material in final_material_list_3:
    
    try:
        score_df_3,variables_df_3,summ_df_3,beta_df_3,Probability_df_3=Model_Output(material,flag_3) #Function will be called to train model
        Master_Score_df_3=pd.concat([Master_Score_df_3,score_df_3])
        Master_Variables_df_3=pd.concat([Master_Variables_df_3,variables_df_3])
        Master_Summary_df_3 = Master_Summary_df_3.append(summ_df_3)
        Master_Beta_df_3=pd.concat([Master_Beta_df_3,beta_df_3])
        Master_prob_df_3=pd.concat([Master_prob_df_3,Probability_df_3])
    except:
        error_list_3.append(material)      #list of Merges for exception came
        
#W+4
        
for material in final_material_list_4:
    
    try:
        score_df_4,variables_df_4,summ_df_4,beta_df_4,Probability_df_4=Model_Output(material,flag_4) #Function will be called to train model
        Master_Score_df_4=pd.concat([Master_Score_df_4,score_df_4])
        Master_Variables_df_4=pd.concat([Master_Variables_df_4,variables_df_4])
        Master_Summary_df_4 = Master_Summary_df_4.append(summ_df_4)
        Master_Beta_df_4=pd.concat([Master_Beta_df_4,beta_df_4])
        Master_prob_df_4=pd.concat([Master_prob_df_4,Probability_df_4])
    except:
        error_list_4.append(material)      #list of Merges for exception came       


#W+8
# for material in final_material_list_8:
    
#     try:
#         score_df_8,variables_df_8,summ_df_8,beta_df_8,Probability_df_8=Model_Output(material,flag_8) #Function will be called to train model
#         Master_Score_df_8=pd.concat([Master_Score_df_8,score_df_8])
#         Master_Variables_df_8=pd.concat([Master_Variables_df_8,variables_df_8])
#         Master_Summary_df_8 = Master_Summary_df_8.append(summ_df_8)
#         Master_Beta_df_8=pd.concat([Master_Beta_df_8,beta_df_8])
#         Master_prob_df_8=pd.concat([Master_prob_df_8,Probability_df_8])
#     except:
#         error_list_8.append(material)      #list of Merges for exception came
    

/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:30: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/

Optimization terminated successfully.
         Current function value: 0.223918
         Iterations 6
[[24  0]
 [ 2  0]]


/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/opt/conda/lib/python3.7/site-packages/sklearn/utils/validation.py:724: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/opt/conda/lib/python3.7/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/opt/conda/lib/python3.7/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/opt/conda/lib/python3.7/site-packages/sklearn/metrics/classification.py:1437: UndefinedM

Optimization terminated successfully.
         Current function value: 0.342406
         Iterations 5
[[23  0]
 [ 3  0]]


/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/opt/conda/lib/python3.7/site-packages/sklearn/utils/validation.py:724: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/opt/conda/lib/python3.7/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/opt/conda/lib/python3.7/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/opt/conda/lib/python3.7/site-packages/sklearn/metrics/classification.py:1437: UndefinedM

...

/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/opt/conda/lib/python3.7/site-packages/sklearn/utils/validation.py:724: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/opt/conda/lib/python3.7/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/opt/conda/lib/python3.7/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/opt/conda/lib/python3.7/site-packages/sklearn/metrics/classification.py:1437: UndefinedM

Optimization terminated successfully.
         Current function value: 0.315102
         Iterations 5
[[23  0]
 [ 3  0]]


/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/opt/conda/lib/python3.7/site-packages/sklearn/utils/validation.py:724: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/opt/conda/lib/python3.7/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/opt/conda/lib/python3.7/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/opt/conda/lib/python3.7/site-packages/sklearn/metrics/classification.py:1437: UndefinedM

Optimization terminated successfully.
         Current function value: 0.502362
         Iterations 4
[[20  0]
 [ 6  0]]


/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
/opt/conda/lib/python3.7/site-packages/sklearn/utils/validation.py:724: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/opt/conda/lib/python3.7/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/opt/conda/lib/python3.7/site-packages/sklearn/metrics/classification.py:1437: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/opt/conda/lib/python3.7/site-packages/sklearn/metrics/classification.py:1437: UndefinedM

In [15]:
Master_Summary_df_1.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+1/average_var_summary_w+1.csv")
Master_Summary_df_1

Average AGED_STOCK_BY_SALES_12_WEEKS  \
Ageing_lead_1_Flag                                         
0.0                                                  NaN   
1.0                                                  NaN   
0.0                                                  NaN   
1.0                                                  NaN   
0.0                                                  NaN   
...                                                  ...   
1.0                                                  NaN   
0.0                                                  NaN   
1.0                                                  NaN   
0.0                                                  NaN   
1.0                                                  NaN   

                    Average AGED_STOCK_BY_SALES_24_WEEKS  \
Ageing_lead_1_Flag                                         
0.0                                                  NaN   
1.0                                                  NaN   
0.0                                                  NaN   
1.0                                                  NaN   
0.0                                                  NaN   
...                                                  ...   
1.0                                                  NaN   
0.0                                                  NaN   
1.0                                                  NaN   
0.0                                                  NaN   
1.0                                                  NaN   

                    Average AGED_STOCK_BY_SALES_4_WEEKS  \
Ageing_lead_1_Flag                                        
0.0                                                 NaN   
1.0                                                 NaN   
0.0                                                 NaN   
1.0                                                 NaN   
0.0                                                 NaN   
...                                                 ...   
1.0                                                 NaN   
0.0                                                 NaN   
1.0                                                 NaN   
0.0                                                 NaN   
1.0                                                 NaN   

                    Average AGEING_FLAG_31_46  Average AGEING_FLAG_46_60  \
Ageing_lead_1_Flag                                                         
0.0                                       NaN                        NaN   
1.0                                       NaN                        NaN   
0.0                                       NaN                        NaN   
1.0                                       NaN                        NaN   
0.0                                       NaN                        NaN   
...                                       ...                        ...   
1.0                                       NaN                        NaN   
0.0                                       NaN                        NaN   
1.0                                       NaN                        NaN   
0.0                                       NaN                        NaN   
1.0                                       NaN                        NaN   

                    Average Avg Cotton Price (Rs/Candy)  \
Ageing_lead_1_Flag                                        
0.0                                        42275.010782   
1.0                                        44128.571429   
0.0                                        42576.930476   
1.0                                        40866.992481   
0.0                                        42541.363212   
...                                                 ...   
1.0                                        40827.050000   
0.0                                        42867.362637   
1.0                                        40775.776557   
0.0                                        42415.001

In [16]:
Master_Score_df_1.to_csv("/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+1/model_performance_w+1.csv")
Master_Score_df_1

Material_Code  Accuracy_Score  F1_Score_train  Recall_Train  Robustness  \
0         A06G20        0.944056        0.000000      0.000000    0.923077   
0         A06G21        0.888112        0.000000      0.000000    0.884615   
0         A06G22        0.902098        0.000000      0.000000    0.923077   
0        A10TP19        0.860140        0.000000      0.000000    0.846154   
0        A10TP20        0.937063        0.470588      0.307692    0.884615   
..           ...             ...             ...           ...         ...   
0       IPB3A510        0.909091        0.000000      0.000000    0.923077   
0       PDT3D801        0.783217        0.000000      0.000000    0.769231   
0         S3J335        0.881119        0.000000      0.000000    0.884615   
0         TB6Y10        0.769231        0.000000      0.000000    0.769231   
0         Z0PW25        0.930070        0.000000      0.000000    0.923077   

    F1_score_test  Recall_Test  Precision_train  Precision_test  \
0             0.0          0.0              0.0             0.0   
0             0.0          0.0              0.0             0.0   
0             0.0          0.0              0.0             0.0   
0             0.0          0.0              0.0             0.0   
0             0.0          0.0              1.0             0.0   
..            ...          ...              ...             ...   
0             0.0          0.0              0.0             0.0   
0             0.0          0.0              0.0             0.0   
0             0.0          0.0              0.0             0.0   
0             0.0          0.0              0.0             0.0   
0             0.0          0.0              0.0             0.0   

    F2_score_train  F2_score_test  
0         0.000000            0.0  
0         0.000000            0.0  
0         0.000000            0.0  
0         0.000000            0.0  
0         0.357143            0.0  
..             ...            ...  
0         0.000000            0.0  
0         0.000000            0.0  
0         0.000000            0.0  
0         0.000000            0.0  
0         0.000000            0.0  

[339 rows x 11 columns]

In [17]:
Master_Variables_df_1.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+1/significant_var_w+1.csv")
Master_Variables_df_1

coef   std err      z  P>|z|    [0.025    0.975]  \
x1 -0.000065  0.000008 -7.771  0.000 -0.000082 -0.000049   
x1 -0.000050  0.000006 -7.813  0.000 -0.000062 -0.000037   
x1 -0.000045  0.000008 -5.940  0.000 -0.000060 -0.000030   
x2 -3.538000  2.248000 -1.574  0.116 -7.944000  0.868000   
x1 -0.000044  0.000006 -7.575  0.000 -0.000055 -0.000033   
..       ...       ...    ...    ...       ...       ...   
x1 -0.000056  0.000007 -7.896  0.000 -0.000070 -0.000042   
x1 -0.000030  0.000005 -6.237  0.000 -0.000039 -0.000020   
x1 -0.000048  0.000006 -7.764  0.000 -0.000060 -0.000036   
x1 -0.000029  0.000005 -6.212  0.000 -0.000039 -0.000020   
x1 -0.000061  0.000008 -7.859  0.000 -0.000077 -0.000046   

                      Variables Material_Code  
x1  Avg Cotton Price (Rs/Candy)        A06G20  
x1  Avg Cotton Price (Rs/Candy)        A06G21  
x1  Avg Cotton Price (Rs/Candy)        A06G22  
x2       LAST_24_WEEK_AVG_SALES        A06G22  
x1  Avg Cotton Price (Rs/Candy)       A10TP19  
..                          ...           ...  
x1  Avg Cotton Price (Rs/Candy)      IPB3A510  
x1  Avg Cotton Price (Rs/Candy)      PDT3D801  
x1  Avg Cotton Price (Rs/Candy)        S3J335  
x1  Avg Cotton Price (Rs/Candy)        TB6Y10  
x1  Avg Cotton Price (Rs/Candy)        Z0PW25  

[1068 rows x 8 columns]

In [18]:
error_df_1=pd.DataFrame({"Material_Code":error_list_1})

error_df_1.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+1/convergence_problm_merges_w+1.csv")
error_df_1

Empty DataFrame
Columns: [Material_Code]
Index: []

In [19]:
Master_Beta_df_1.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+1/Beta_values_w+1.csv")
Master_Beta_df_1

index                    Variables   Beta_Values  Material
0       0  Avg Cotton Price (Rs/Candy) -6.537557e-05    A06G20
0       0  Avg Cotton Price (Rs/Candy) -4.976162e-05    A06G21
0       0  Avg Cotton Price (Rs/Candy) -5.342252e-05    A06G22
1       1       LAST_24_WEEK_AVG_SALES -3.588745e-10    A06G22
0       0  Avg Cotton Price (Rs/Candy) -4.386251e-05   A10TP19
..    ...                          ...           ...       ...
0       0  Avg Cotton Price (Rs/Candy) -5.575210e-05  IPB3A510
0       0  Avg Cotton Price (Rs/Candy) -2.965020e-05  PDT3D801
0       0  Avg Cotton Price (Rs/Candy) -4.811132e-05    S3J335
0       0  Avg Cotton Price (Rs/Candy) -2.948490e-05    TB6Y10
0       0  Avg Cotton Price (Rs/Candy) -6.126822e-05    Z0PW25

[1068 rows x 4 columns]

In [20]:
Master_prob_df_1.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+1/all_data_w+1.csv")
Master_prob_df_1

index Monday_Dates Material Code  Total Quantity  Transaction Count  \
0   81468   2021-01-25        A06G20             0.0                0.0   
1   81818   2021-02-01        A06G20             0.0                0.0   
2   82528   2021-02-08        A06G20             0.0                0.0   
3   83022   2021-02-15        A06G20             0.0                0.0   
4   83474   2021-02-22        A06G20             0.0                0.0   
..    ...          ...           ...             ...                ...   
18  90237   2021-05-31        Z0PW25             0.0                0.0   
19  90682   2021-06-07        Z0PW25             0.0                0.0   
20  91237   2021-06-14        Z0PW25             0.0                0.0   
21  91769   2021-06-21        Z0PW25             0.0                0.0   
22  92008   2021-06-28        Z0PW25             0.0                0.0   

    Count_of_unique_group_code  Region_Count  Unique_Sales_Plant_Count  \
0                          0.0           0.0                       0.0   
1                          0.0           0.0                       0.0   
2                          0.0           0.0                       0.0   
3                          0.0           0.0                       0.0   
4                          0.0           0.0                       0.0   
..                         ...           ...                       ...   
18                         0.0           0.0                       0.0   
19                         0.0           0.0                       0.0   
20                         0.0           0.0                       0.0   
21                         0.0           0.0                       0.0   
22                         0.0           0.0                       0.0   

    COUNT_DEPOT(EXCISE)  COUNT_EXPORT PORT  ...  Avg Cotton Price (Rs/Candy)  \
0                   0.0                0.0  ...                 45000.000000   
1                   0.0                0.0  ...                 45000.000000   
2                   0.0                0.0  ...                 46500.000000   
3                   0.0                0.0  ...                 46500.000000   
4                   0.0                0.0  ...                 46500.000000   
..                  ...                ...  ...                          ...   
18                  0.0                0.0  ...                 45500.000000   
19                  0.0                0.0  ...                 45928.571429   
20                  0.0                0.0  ...                 46000.000000   
21                  0.0                0.0  ...                 48500.000000   
22                  0.0                0.0  ...                 49500.000000   

    Avg of Crude_Price  Ageing_lead_1_Flag  Ageing_lead_2_Flag  \
0               55.548                 0.0                 0.0   
1               55.826                 0.0                 0.0   
2               57.762                 0.0                 0.0   
3               60.764                 0.0                 0.0   
4               63.606                 0.0                 0.0   
..                 ...                 ...                 ...   
18              68.510                 0.0                 0.0   
19              70.856                 0.0                 0.0   
20              71.964                 0.0                 0.0   
21              58.854                 0.0                 NaN   
22              74.854                 NaN                 NaN   

    Ageing_lead_3_Flag  Ageing_lead_4_Flag  Ageing_lead_8_Flag  \
0                  0.0                 0.0                 0.0   
1                  0.0                 0.0                 0.0   
2                  0.0                 0.0                 0.0   
3                  0.0                 0.0                 0.0   
4                  0.0                 0.0                 0.0   
..                 ...                 ...                 ...  

In [21]:
Master_Summary_df_2.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+2/average_var_summary_w+2.csv")
Master_Variables_df_2.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+2/significant_var_w+2.csv")
Master_Score_df_2.to_csv("/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+2/model_performance_w+2.csv")
error_df_2=pd.DataFrame({"Material_Code":error_list_2})

error_df_2.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+2/convergence_problm_merges_w+2.csv")
Master_Beta_df_2.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+2/Beta_values_w+2.csv")
Master_prob_df_2.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+2/all_data_w+2.csv")


In [22]:
Master_Summary_df_3.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+3/average_var_summary_w+3.csv")
Master_Variables_df_3.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+3/significant_var_w+3.csv")
Master_Score_df_3.to_csv("/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+3/model_performance_w+3.csv")
error_df_3=pd.DataFrame({"Material_Code":error_list_3})
#error_df_3["Model_Status_w+3"]="NOT CONVERGED"
error_df_3.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+3/convergence_problm_merges_w+3.csv")
Master_Beta_df_3.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+3/Beta_values_w+3.csv")
Master_prob_df_3.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+3/all_data_w+3.csv")


In [23]:
Master_Summary_df_4.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+4/average_var_summary_w+4.csv")
Master_Variables_df_4.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+4/significant_var_w+4.csv")
Master_Score_df_4.to_csv("/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+4/model_performance_w+4.csv")
error_df_4=pd.DataFrame({"Material_Code":error_list_4})
#error_df_4["Model_Status_w+4"]="NOT CONVERGED"
error_df_4.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+4/convergence_problm_merges_w+4.csv")
Master_Beta_df_4.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+4/Beta_values_w+4.csv")
Master_prob_df_4.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+4/all_data_w+4.csv")


In [24]:
#Master_Score_df_1.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/W+1/model_performance_w+1.csv")
# def total(r):
#         if (r["Accuracy_Score"]>0.50) & (r["F1_Score_train_Flag_0"] >0.25) & (r["F1_Score_train_Flag_1"]>0.25):
#             return "RELIABLE MODEL"
        
#         else:
#             return "NON RELIABLE MODEL"
          
# Master_Score_df_1['Model_Status_w+1'] = Master_Score_df_1.apply(total, axis=1)
# Master_Score_df_2['Model_Status_w+2'] = Master_Score_df_2.apply(total, axis=1)
# Master_Score_df_3['Model_Status_w+3'] = Master_Score_df_3.apply(total, axis=1)
# Master_Score_df_4['Model_Status_w+4'] = Master_Score_df_4.apply(total, axis=1)

Model_status_1=pd.concat([Master_Score_df_1[["Material_Code","F1_Score_train","Recall_Train","Precision_train","F2_score_train","F1_score_test","Recall_Test","Precision_test","F2_score_test"]],class_imb_df_1,error_df_1])
Model_status_2=pd.concat([Master_Score_df_2[["Material_Code","F1_Score_train","Recall_Train","Precision_train","F2_score_train","F1_score_test","Recall_Test","Precision_test","F2_score_test"]],class_imb_df_2,error_df_2])
Model_status_3=pd.concat([Master_Score_df_3[["Material_Code","F1_Score_train","Recall_Train","Precision_train","F2_score_train","F1_score_test","Recall_Test","Precision_test","F2_score_test"]],class_imb_df_3,error_df_3])
Model_status_4=pd.concat([Master_Score_df_4[["Material_Code","F1_Score_train","Recall_Train","Precision_train","F2_score_train","F1_score_test","Recall_Test","Precision_test","F2_score_test"]],class_imb_df_4,error_df_4])

Model_status_1=Model_status_1.rename(columns={"Material_Code":"Material Code","F1_Score_train":"F1_Score_train_W+1","Recall_Train":"Recall_Train_W+1","Precision_train":"Precision_train_W+1","F2_score_train":"F2_score_train_W+1","F1_score_test":"F1_score_test_W+1","Recall_Test":"Recall_Test_W+1","Precision_test":"Precision_test_W+1","F2_score_test":"F2_score_test_W+1"})
Model_status_2=Model_status_2.rename(columns={"Material_Code":"Material Code","F1_Score_train":"F1_Score_train_W+2","Recall_Train":"Recall_Train_W+2","Precision_train":"Precision_train_W+2","F2_score_train":"F2_score_train_W+2","F1_score_test":"F1_score_test_W+2","Recall_Test":"Recall_Test_W+2","Precision_test":"Precision_test_W+2","F2_score_test":"F2_score_test_W+2"})
Model_status_3=Model_status_3.rename(columns={"Material_Code":"Material Code","F1_Score_train":"F1_Score_train_W+3","Recall_Train":"Recall_Train_W+3","Precision_train":"Precision_train_W+3","F2_score_train":"F2_score_train_W+3","F1_score_test":"F1_score_test_W+3","Recall_Test":"Recall_Test_W+3","Precision_test":"Precision_test_W+3","F2_score_test":"F2_score_test_W+3"})
Model_status_4=Model_status_4.rename(columns={"Material_Code":"Material Code","F1_Score_train":"F1_Score_train_W+4","Recall_Train":"Recall_Train_W+4","Precision_train":"Precision_train_W+4","F2_score_train":"F2_score_train_W+4","F1_score_test":"F1_score_test_W+4","Recall_Test":"Recall_Test_W+4","Precision_test":"Precision_test_W+4","F2_score_test":"F2_score_test_W+4"})

/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:14: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  
/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:15: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  from ipykernel import kernelapp as app
/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:16: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, 

In [25]:
Master_prob_df_1=Master_prob_df_1.rename(columns={"PREDICTED_NON_AGEING_PROBABILITY":"PREDICTED_NON_AGEING_PROBABILITY_W+1",
                                "PREDICTED_AGEING_PROBABILITY":"PREDICTED_AGEING_PROBABILITY_W+1",
                                "PREDICTED_FLAG":"PREDICTED_FLAG(W+1)"})
Master_prob_df_2=Master_prob_df_2.rename(columns={"PREDICTED_NON_AGEING_PROBABILITY":"PREDICTED_NON_AGEING_PROBABILITY_W+2",
                                "PREDICTED_AGEING_PROBABILITY":"PREDICTED_AGEING_PROBABILITY_W+2",
                                "PREDICTED_FLAG":"PREDICTED_FLAG(W+2)"})
Master_prob_df_3=Master_prob_df_3.rename(columns={"PREDICTED_NON_AGEING_PROBABILITY":"PREDICTED_NON_AGEING_PROBABILITY_W+3",
                                "PREDICTED_AGEING_PROBABILITY":"PREDICTED_AGEING_PROBABILITY_W+3",
                                "PREDICTED_FLAG":"PREDICTED_FLAG(W+3)"})
Master_prob_df_4=Master_prob_df_4.rename(columns={"PREDICTED_NON_AGEING_PROBABILITY":"PREDICTED_NON_AGEING_PROBABILITY_W+4",
                                "PREDICTED_AGEING_PROBABILITY":"PREDICTED_AGEING_PROBABILITY_W+4",
                                "PREDICTED_FLAG":"PREDICTED_FLAG(W+4)"})

In [26]:
master_data_prob=var_new_1.copy()
master_data_prob=master_data_prob.loc[master_data_prob["Monday_Dates"]>=train_stop_date]
master_data_prob=master_data_prob.drop(columns=["Ageing_lead_1_Flag","Ageing_lead_2_Flag","Ageing_lead_3_Flag","Ageing_lead_4_Flag","Ageing_lead_8_Flag"])
master_data_prob=pd.merge(master_data_prob,
                          Master_prob_df_1[["Monday_Dates","Material Code","Ageing_lead_1_Flag","PREDICTED_NON_AGEING_PROBABILITY_W+1","PREDICTED_AGEING_PROBABILITY_W+1","PREDICTED_FLAG(W+1)"]],
                         how="left",on=["Monday_Dates","Material Code"])
master_data_prob=pd.merge(master_data_prob,Model_status_1,how="left",on=["Material Code"])
master_data_prob=pd.merge(master_data_prob,
                          Master_prob_df_2[["Monday_Dates","Material Code","Ageing_lead_2_Flag","PREDICTED_NON_AGEING_PROBABILITY_W+2","PREDICTED_AGEING_PROBABILITY_W+2","PREDICTED_FLAG(W+2)"]],
                         how="left",on=["Monday_Dates","Material Code"])
master_data_prob=pd.merge(master_data_prob,Model_status_2,how="left",on=["Material Code"])
master_data_prob=pd.merge(master_data_prob,
                          Master_prob_df_3[["Monday_Dates","Material Code","Ageing_lead_3_Flag","PREDICTED_NON_AGEING_PROBABILITY_W+3","PREDICTED_AGEING_PROBABILITY_W+3","PREDICTED_FLAG(W+3)"]],
                         how="left",on=["Monday_Dates","Material Code"])
master_data_prob=pd.merge(master_data_prob,Model_status_3,how="left",on=["Material Code"])
master_data_prob=pd.merge(master_data_prob,
                          Master_prob_df_4[["Monday_Dates","Material Code","Ageing_lead_4_Flag","PREDICTED_NON_AGEING_PROBABILITY_W+4","PREDICTED_AGEING_PROBABILITY_W+4","PREDICTED_FLAG(W+4)"]],
                         how="left",on=["Monday_Dates","Material Code"])
master_data_prob=pd.merge(master_data_prob,Model_status_4,how="left",on=["Material Code"])
master_data_prob

Monday_Dates Material Code  Total Quantity  Transaction Count  \
0       2021-01-25         Z5L25           0.000                0.0   
1       2021-01-25        WIRL30         405.390               31.0   
2       2021-01-25      I3F22505           0.000                0.0   
3       2021-01-25       ZB3A350           0.000                0.0   
4       2021-01-25        S3J335           0.000                0.0   
...            ...           ...             ...                ...   
11127   2021-06-28        A3F611           0.000                0.0   
11128   2021-06-28         Z5L20         117.902                6.0   
11129   2021-06-28         Z5L25           0.000                0.0   
11130   2021-06-28      IKD4F501           0.000                0.0   
11131   2021-06-28        S3A135        4117.624              236.0   

       Count_of_unique_group_code  Region_Count  Unique_Sales_Plant_Count  \
0                             0.0           0.0                       0.0   
1                             6.0           3.0                       2.0   
2                             0.0           0.0                       0.0   
3                             0.0           0.0                       0.0   
4                             0.0           0.0                       0.0   
...                           ...           ...                       ...   
11127                         0.0           0.0                       0.0   
11128                         1.0           1.0                       2.0   
11129                         0.0           0.0                       0.0   
11130                         0.0           0.0                       0.0   
11131                        21.0           4.0                       5.0   

       COUNT_DEPOT(EXCISE)  COUNT_EXPORT PORT  COUNT_LOGICAL PLANT  ...  \
0                      0.0                0.0                  0.0  ...   
1                      0.0                0.0                 15.0  ...   
2                      0.0                0.0                  0.0  ...   
3                      0.0                0.0                  0.0  ...   
4                      0.0                0.0                  0.0  ...   
...                    ...                ...                  ...  ...   
11127                  0.0                0.0                  0.0  ...   
11128                  0.0                0.0                  3.0  ...   
11129                  0.0                0.0                  0.0  ...   
11130                  0.0                0.0                  0.0  ...   
11131                 39.0                0.0                  0.0  ...   

       PREDICTED_AGEING_PROBABILITY_W+4  PREDICTED_FLAG(W+4)  \
0                              0.001157                  0.0   
1                              0.097683                  0.0   
2                              0.063366                  0.0   
3                                   NaN                  NaN   
4                              0.084108                  0.0   
...                                 ...                  ...   
11127                          0.034422                  0.0   
11128                          0.133248                  0.0   
11129                          0.006254                  0.0   
11130                          0.156998                  0.0   
11131                          0.001131                  0.0   

       F1_Score_train_W+4  F1_score_test_W+4  F2_score_test_W+4  \
0                0.682927           0.769231           0.675676   
1                0.000000           0.000000           0.000000   
2                0.000000           0.000000           0.000000   
3                     NaN                NaN                NaN   
4                0.000000           0.000000           0.000000   
...                   ...                ...                ...   
11127            0.000000           0.000000           0.000000   
11128            0.000

In [27]:
master_data_prob.columns

Index(['Monday_Dates', 'Material Code', 'Total Quantity', 'Transaction Count',
       'Count_of_unique_group_code', 'Region_Count',
       'Unique_Sales_Plant_Count', 'COUNT_DEPOT(EXCISE)', 'COUNT_EXPORT PORT',
       'COUNT_LOGICAL PLANT',
       ...
       'PREDICTED_AGEING_PROBABILITY_W+4', 'PREDICTED_FLAG(W+4)',
       'F1_Score_train_W+4', 'F1_score_test_W+4', 'F2_score_test_W+4',
       'F2_score_train_W+4', 'Precision_test_W+4', 'Precision_train_W+4',
       'Recall_Test_W+4', 'Recall_Train_W+4'],
      dtype='object', length=105)

In [28]:
master_data_prob.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/Combined_prob_data.csv")

In [29]:
output_df_all=master_data_prob[["Monday_Dates","Material Code","PREDICTED_AGEING_PROBABILITY_W+1","PREDICTED_AGEING_PROBABILITY_W+2","PREDICTED_AGEING_PROBABILITY_W+3","PREDICTED_AGEING_PROBABILITY_W+4","Recall_Train_W+1","Recall_Train_W+2","Recall_Train_W+3","Recall_Train_W+4","Recall_Test_W+1","Recall_Test_W+2","Recall_Test_W+3","Recall_Test_W+4","F1_Score_train_W+1","F1_Score_train_W+2","F1_Score_train_W+3","F1_Score_train_W+4","F1_score_test_W+1","F1_score_test_W+2","F1_score_test_W+3","F1_score_test_W+4","Precision_train_W+1","Precision_train_W+2","Precision_train_W+3","Precision_train_W+4","Precision_test_W+1","Precision_test_W+2","Precision_test_W+3","Precision_test_W+4","F2_score_train_W+1","F2_score_train_W+2","F2_score_train_W+3","F2_score_train_W+4","F2_score_test_W+1","F2_score_test_W+2","F2_score_test_W+3","F2_score_test_W+4"]]
output_df_all

Monday_Dates Material Code  PREDICTED_AGEING_PROBABILITY_W+1  \
0       2021-01-25         Z5L25                          0.004299   
1       2021-01-25        WIRL30                          0.121856   
2       2021-01-25      I3F22505                          0.065041   
3       2021-01-25       ZB3A350                               NaN   
4       2021-01-25        S3J335                          0.102937   
...            ...           ...                               ...   
11127   2021-06-28        A3F611                          0.035611   
11128   2021-06-28         Z5L20                          0.102354   
11129   2021-06-28         Z5L25                          0.011458   
11130   2021-06-28      IKD4F501                          0.050301   
11131   2021-06-28        S3A135                          0.156883   

       PREDICTED_AGEING_PROBABILITY_W+2  PREDICTED_AGEING_PROBABILITY_W+3  \
0                              0.001221                          0.000688   
1                              0.110137                          0.110684   
2                              0.064919                          0.063961   
3                                   NaN                               NaN   
4                              0.096852                          0.090250   
...                                 ...                               ...   
11127                          0.034910                          0.034479   
11128                          0.250853                          0.125539   
11129                          0.010950                          0.006827   
11130                          0.080143                          0.128640   
11131                          0.212956                          0.037788   

       PREDICTED_AGEING_PROBABILITY_W+4  Recall_Train_W+1  Recall_Train_W+2  \
0                              0.001157          0.714286          0.729167   
1                              0.097683          0.055556          0.055556   
2                              0.063366          0.000000          0.000000   
3                                   NaN               NaN               NaN   
4                              0.084108          0.000000          0.000000   
...                                 ...               ...               ...   
11127                          0.034422          0.000000          0.000000   
11128                          0.133248          0.000000          0.181818   
11129                          0.006254          0.714286          0.729167   
11130                          0.156998          0.731707          0.609756   
11131                          0.001131          0.658537          0.658537   

       Recall_Train_W+3  Recall_Train_W+4  ...  Precision_test_W+3  \
0              0.638298          0.595745  ...               0.875   
1              0.000000          0.000000  ...               0.000   
2              0.000000          0.000000  ...               0.000   
3                   NaN               NaN  ...                 NaN   
4              0.000000          0.000000  ...               0.000   
...                 ...               ...  ...                 ...   
11127          0.000000          0.000000  ...               0.000   
11128          0.000000          0.000000  ...               0.000   
11129          0.638298          0.595745  ...               0.875   
11130          0.512195          0.463415  ...               1.000   
11131          0.609756          0.585366  ...               0.400   

       Precision_test_W+4  F2_score_train_W+1  F2_score_train_W+2  \
0                1.000000            0.732218            0.741525   
1                0.000000            0.068493            0.068493   
2                0.000000            0.000000            0.000000   
3                     NaN                 NaN                 NaN   
4                0.000000            0.000000            0.000000   
...                   ...           

In [30]:
#output_df_latest.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/Dec_20_output_thr300kg.csv")
#output_df_all.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/Static_pred_output.csv")

In [31]:
pd.options.display.max_rows = None
pd.options.display.max_columns = None

In [32]:
df_end=output_df_all.loc[output_df_all["Monday_Dates"]==end_date]


In [33]:
df_end["R&P_W+1"]=0.7*df_end["Recall_Train_W+1"]+0.3*df_end["Precision_train_W+1"]
df_end["R&P_W+2"]=0.7*df_end["Recall_Train_W+2"]+0.3*df_end["Precision_train_W+2"]
df_end["R&P_W+3"]=0.7*df_end["Recall_Train_W+3"]+0.3*df_end["Precision_train_W+3"]
df_end["R&P_W+4"]=0.7*df_end["Recall_Train_W+4"]+0.3*df_end["Precision_train_W+4"]

df_end["Rel_Criteria_W+1"]=np.where(df_end['R&P_W+1']>=0.4,"RELIABLE", "NON_RELIABLE")
df_end["Rel_Criteria_W+2"]=np.where(df_end['R&P_W+2']>=0.4,"RELIABLE", "NON_RELIABLE")
df_end["Rel_Criteria_W+3"]=np.where(df_end['R&P_W+3']>=0.4,"RELIABLE", "NON_RELIABLE")
df_end["Rel_Criteria_W+4"]=np.where(df_end['R&P_W+4']>=0.4,"RELIABLE", "NON_RELIABLE")
#####
df_end['Model_Avail_W+1'] = np.where(df_end['PREDICTED_AGEING_PROBABILITY_W+1'].isnull(),"Not_Avail", "Avail")
df_end['Model_Avail_W+2'] = np.where(df_end['PREDICTED_AGEING_PROBABILITY_W+2'].isnull(),"Not_Avail", "Avail")
df_end['Model_Avail_W+3'] = np.where(df_end['PREDICTED_AGEING_PROBABILITY_W+3'].isnull(),"Not_Avail", "Avail")
df_end['Model_Avail_W+4'] = np.where(df_end['PREDICTED_AGEING_PROBABILITY_W+4'].isnull(),"Not_Avail", "Avail")
####
df_end['Avail_flag_W+1'] = np.where(df_end['PREDICTED_AGEING_PROBABILITY_W+1'].isnull(),0,1)
df_end['Avail_flag_W+2'] = np.where(df_end['PREDICTED_AGEING_PROBABILITY_W+2'].isnull(),0,1)
df_end['Avail_flag_W+3'] = np.where(df_end['PREDICTED_AGEING_PROBABILITY_W+3'].isnull(),0,1)
df_end['Avail_flag_W+4'] = np.where(df_end['PREDICTED_AGEING_PROBABILITY_W+4'].isnull(),0,1)

df_end["Weekly_Pred_Number"]= df_end['Avail_flag_W+1']+df_end['Avail_flag_W+2']+df_end['Avail_flag_W+3']+df_end['Avail_flag_W+4']


col = df_end.loc[: , "R&P_W+1":"R&P_W+4"]
df_end['Aggregated_Confidence'] = col.mean(axis=1)



/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documenta

In [34]:
##Dealing with Null values for calculations
df_end["PREDICTED_AGEING_PROBABILITY_W+1_temp"]=df_end["PREDICTED_AGEING_PROBABILITY_W+1"].fillna(0)
df_end["PREDICTED_AGEING_PROBABILITY_W+2_temp"]=df_end["PREDICTED_AGEING_PROBABILITY_W+2"].fillna(0)
df_end["PREDICTED_AGEING_PROBABILITY_W+3_temp"]=df_end["PREDICTED_AGEING_PROBABILITY_W+3"].fillna(0)
df_end["PREDICTED_AGEING_PROBABILITY_W+4_temp"]=df_end["PREDICTED_AGEING_PROBABILITY_W+4"].fillna(0)

df_end["R&P_W+1_temp"]=df_end["R&P_W+1"].fillna(0)
df_end["R&P_W+2_temp"]=df_end["R&P_W+2"].fillna(0)
df_end["R&P_W+3_temp"]=df_end["R&P_W+3"].fillna(0)
df_end["R&P_W+4_temp"]=df_end["R&P_W+4"].fillna(0)


/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead



In [35]:
df_end["Aggreagted_Probability"]=(df_end["PREDICTED_AGEING_PROBABILITY_W+1_temp"]*df_end["R&P_W+1_temp"]+
                                 df_end["PREDICTED_AGEING_PROBABILITY_W+2_temp"]*df_end["R&P_W+2_temp"]+
                                 df_end["PREDICTED_AGEING_PROBABILITY_W+3_temp"]*df_end["R&P_W+3_temp"]+
                                 df_end["PREDICTED_AGEING_PROBABILITY_W+4_temp"]*df_end["R&P_W+4_temp"])/(df_end["R&P_W+1_temp"]+df_end["R&P_W+2_temp"]+df_end["R&P_W+3_temp"]+df_end["R&P_W+4_temp"])
df_end.loc[df_end['Weekly_Pred_Number']<2,['Aggregated_Confidence','Aggreagted_Probability']] = np.nan
df_end['Aggregated_Model_Avail'] = np.where(df_end['Aggreagted_Probability'].isnull(),"Not_Avail", "Avail")


/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.
/opt/conda/lib/python3.7/site-packages/pandas/core/indexing.py:494: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s
/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in t

In [36]:
df_ready_output=df_end[["Monday_Dates","Material Code","Aggregated_Model_Avail","Aggreagted_Probability","Aggregated_Confidence",
                      "Model_Avail_W+1","PREDICTED_AGEING_PROBABILITY_W+1","R&P_W+1","Rel_Criteria_W+1",
                       "Model_Avail_W+2","PREDICTED_AGEING_PROBABILITY_W+2","R&P_W+2","Rel_Criteria_W+2",
                       "Model_Avail_W+3","PREDICTED_AGEING_PROBABILITY_W+3","R&P_W+3","Rel_Criteria_W+3",
                       "Model_Avail_W+4","PREDICTED_AGEING_PROBABILITY_W+4","R&P_W+4","Rel_Criteria_W+4"]]

In [37]:
df_ready_output

Monday_Dates Material Code Aggregated_Model_Avail  \
10648   2021-06-28       IBT4L29              Not_Avail   
10649   2021-06-28      IBT3L301              Not_Avail   
10650   2021-06-28        I3L301              Not_Avail   
10651   2021-06-28       IBT4G35              Not_Avail   
10652   2021-06-28       IBT4L30                  Avail   
10653   2021-06-28     ISNB3A500              Not_Avail   
10654   2021-06-28       IBT4L35              Not_Avail   
10655   2021-06-28       IBT4Q30              Not_Avail   
10656   2021-06-28       IBT4G30                  Avail   
10657   2021-06-28        Z3E201              Not_Avail   
10658   2021-06-28      ICDB4F39              Not_Avail   
10659   2021-06-28        I3J301                  Avail   
10660   2021-06-28      ICDB5A39              Not_Avail   
10661   2021-06-28         I4A35                  Avail   
10662   2021-06-28     SPB4QT5T1              Not_Avail   
10663   2021-06-28       IBS4A30                  Avail   
10664   2021-06-28      IBS3A301              Not_Avail   
10665   2021-06-28         I4A30                  Avail   
10666   2021-06-28      IBL3A500              Not_Avail   
10667   2021-06-28       IBT5L29              Not_Avail   
10668   2021-06-28       IBT5L30              Not_Avail   
10669   2021-06-28        I3F302              Not_Avail   
10670   2021-06-28       IBT5L35              Not_Avail   
10671   2021-06-28      ICDB4F50              Not_Avail   
10672   2021-06-28      I3D22505              Not_Avail   
10673   2021-06-28        TB6Y10              Not_Avail   
10674   2021-06-28      IBT3G301              Not_Avail   
10675   2021-06-28     ACDB06F20              Not_Avail   
10676   2021-06-28         Z3A20              Not_Avail   
10677   2021-06-28         Z2F20                  Avail   
10678   2021-06-28      ICDB4A51              Not_Avail   
10679   2021-06-28     ILTQ3A501              Not_Avail   
10680   2021-06-28     ACDB3P201              Not_Avail   
10681   2021-06-28         Z2A40                  Avail   
10682   2021-06-28         Z2A30                  Avail   
10683   2021-06-28         Z2A20                  Avail   
10684   2021-06-28     ACDB3P211              Not_Avail   
10685   2021-06-28       Z0PPW35              Not_Avail   
10686   2021-06-28       Z0PPW25              Not_Avail   
10687   2021-06-28       WS4A145                  Avail   
10688   2021-06-28     ADTB06Q20              Not_Avail   
10689   2021-06-28     ACDB06P20              Not_Avail   
10690   2021-06-28         Z2D51                  Avail   
10691   2021-06-28         Z2D40                  Avail   
10692   2021-06-28         Z2D50                  Avail   
10693   2021-06-28        Z2FW30              Not_Avail   
10694   2021-06-28         A7S60              Not_Avail   
10695   2021-06-28        Z2FW25              Not_Avail   
10696   2021-06-28        Z0PW25              Not_Avail   
10697   2021-06-28         Z2F55                  Avail   
10698   2021-06-28         Z2F51              Not_Avail   
10699   2021-06-28         Z2F50                  Avail   
10700   2021-06-28         Z2F40              Not_Avail   
10701   2021-06-28         Z2F30              Not_Avail   
10702   2021-06-28        A7S601              Not_Avail   
10703   2021-06-28         Z2F25              Not_Avail   
10704   2021-06-28        Z3A201                  Avail   
10705   2021-06-28      ICDB4A39                  Avail   
10706   2021-06-28      IOG4F498              Not_Avail   
10707   2021-06-28      ICDB3A51              Not_Avail   
10708   2021-06-28     IB5RTQ450                  Avail   
10709   2021-06-28        I4A4D0              Not_Avail   
10710   2021-06-28     IB4RTQ450              Not_Avail   
10711   2021-06-28     IB4G42F03              Not_Avail   
10712   2021-06-28        IB4A30              Not_Avail   
10713   2021-06-28      I4F23505              Not_Avail   
10714   2021-06-28     IB3F01805              Not_Ava

In [38]:
df_ready_output.to_csv(r"/home/jovyan/ageing-inventory-project/Integrated_Pipeline/Regular_Merges/Results/Regular_merges_ready_July21_preds.csv")